REDBUS STATE BY STATE BUS DETAILS:

In [4]:
#Importing Libraries

from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.action_chains import ActionChains
import time
import pandas as pd

In [5]:
#Initializing scroll function 

def scroll_to_load(driver, scroll_wait_sec):
    
    while True:            
        time1 = time.time()  #get current time before scrolling
        init_height = driver.execute_script("return document.body.scrollHeight") #To get initial height of page

        while True:        
            time.sleep(.001)  # while scrolling it waits for  0.01 sec for each scroll
            new_height = driver.execute_script("return document.body.scrollHeight") #to get updated height of page after waiting
            driver.execute_script("window.scrollTo(0, document.body.scrollHeight);") #scroll to bottom of page
            time2 = time.time()    #get the current time after scrolling
            if (time2 - time1) > scroll_wait_sec: # total scrolling time should be greater than waited scroll time 
                break
            if new_height != init_height: 
                break
            
        if (time2 - time1) > scroll_wait_sec: 
            break

KERALA BUS 

In [4]:

#read csv file
df=pd.read_csv("kerala_routes.csv")
df

Route name  \
0            Bangalore to Kozhikode   
1            Kozhikode to Ernakulam   
2            Kozhikode to Bangalore   
3            Ernakulam to Kozhikode   
4               Kozhikode to Mysore   
5   Kozhikode to Thiruvananthapuram   
6    Bangalore to Kalpetta (kerala)   
7               Mysore to Kozhikode   
8    Kalpetta (kerala) to Bangalore   
9             Kozhikode to Thrissur   
10  Thiruvananthapuram to Kozhikode   
11              Bangalore to Kannur   
12            Kozhikode to Kottayam   
13              Kannur to Bangalore   
14            Kottayam to Kozhikode   
15            Thrissur to Kozhikode   
16   Kozhikode to Kalpetta (kerala)   
17               Coimbatore to Ooty   
18   Kalpetta (kerala) to Kozhikode   

                                           Route link  
0   https://www.redbus.in/bus-tickets/bangalore-to...  
1   https://www.redbus.in/bus-tickets/kozhikode-to...  
2   https://www.redbus.in/bus-tickets/kozhikode-to...  
3   https://www.redbus.in/bus-tickets/ernakulam-to...  
4   https://www.redbus.in/bus-tickets/kozhikode-to...  
5   https://www.redbus.in/bus-tickets/kozhikode-to...  
6   https://www.redbus.in/bus-tickets/bangalore-to...  
7   https://www.redbus.in/bus-tickets/mysore-to-ko...  
8   https://www.redbus.in/bus-tickets/kalpetta-to-...  
9   https://www.redbus.in/bus-tickets/kozhikode-to...  
10  https://www.redbus.in/bus-tickets/thiruvananth...  
11  https://www.redbus.in/bus-tickets/bangalore-to...  
12  https://www.redbus.in/bus-tickets/kozhikode-to...  
13  https://www.redbus.in/bus-tickets/kannur-to-ba...  
14  https://www.redbus.in/bus-tickets/kottayam-to-...  
15  https://www.redbus.in/bus-tickets/thrissur-to-...  
16  https://www.redbus.in/bus-tickets/kozhikode-to...  
17  https://www.redbus.in/bus-tickets/coimbatore-t...  
18  https://www.redbus.in/bus-tickets/kalpetta-to-...

KERALA BUS DETAILS

In [12]:
driver = webdriver.Chrome()

#Creating a list to store bus details

bus_details = []

#looping the each route links in the  dataframe :

for i in df["Route link"]:

    driver.get(i) #loading the each links

    full_url = driver.current_url  
    driver.get(full_url + f'&onward=14-Aug-2024') #Appends a date parameter to the URL and reloads the page.

    time.sleep(2)  # Let the page load
    driver.maximize_window()
    
    # To get route name and route links
    try:
        route_name = driver.find_element(By.CLASS_NAME, 'D136_h1').text
        route_link = driver.current_url
    except Exception as e:
        print(f"Error retrieving route name or link: {e}")
        continue
    
    # Initialize WebDriverWait
    wait = WebDriverWait(driver, 20)  # Increased timeout

    # Wait for buttons to be visible and click them
    try:
        govt_buttons = wait.until(EC.visibility_of_all_elements_located((By.XPATH, './/div[@class="button"]')))
        for govt_button in govt_buttons[::-1]:
                driver.execute_script("window.scrollTo(0, 330);")
                govt_button.click()
                time.sleep(2)
                
    except Exception as e:
        print(f"Error waiting for buttons: {e}")
        continue

    # Scroll down to load more buses
    scroll_to_load(driver, 10)

    # Wait until all  bus items  present
    try:
        wait.until(EC.presence_of_all_elements_located((By.CLASS_NAME, 'bus-item')))
        containers = driver.find_elements(By.CLASS_NAME, 'bus-item')
        for container in containers:
            try:
                bus_names = container.find_element(By.XPATH, './/div[@class="travels lh-24 f-bold d-color"]').text
                bus_type = container.find_element(By.XPATH, './/div[@class="bus-type f-12 m-top-16 l-color evBus"]').text
                departure_time = container.find_element(By.XPATH, './/div[@class="dp-time f-19 d-color f-bold"]').text
                duration = container.find_element(By.XPATH, './/div[@class="dur l-color lh-24"]').text
                reaching_time = container.find_element(By.XPATH, './/div[@class="bp-time f-19 d-color disp-Inline"]').text
                star_rating = container.find_element(By.XPATH,".//div[@class='column-six p-right-10 w-10 fl']").text
                price = container.find_element(By.XPATH, './/div[@class="fare d-block"]').text
                seat_availability = container.find_element(By.XPATH, './/div[contains(@class,"seat-left")]').text

                 
                bus_details.append({
                    "bus_name": bus_names,
                    "bus_type": bus_type,
                    "departure_time": departure_time,
                    "duration": duration,
                    "reaching_time": reaching_time,
                    "star_rating": star_rating,
                    "price": price,
                    "seat_availability": seat_availability,
                    "route_name": route_name,
                    "route_link": route_link
                })
            except Exception as e:
                print(f"Error extracting details: {e}")
    except Exception as e:
        print(f"Error waiting for bus items: {e}")

    

# Print the collected bus details
print(bus_details)



Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

[{'bus_name': 'KSRTC (Kerala) - 1029', 'bus_type': 'Super Fast Non AC Seater (2+3)', 'departure_time': '00:00', 'duration': '05h 35m', 'reaching_time': '05:35', 'star_rating': '3.0', 'price': 'INR 269', 'seat_availability': '49 Seats available', 'route_name': 'Kozhikode to Ernakulam Bus', 'route_link': 'https://www.redbus.in/bus-tickets/kozhikode-to-ernakulam?fromCityId=74661&toCityId=216&fromCityName=Kozhikode&toCityName=Ernakulam&busType=Any&srcCountry=IND&destCountry=IND&onward=13-Aug-2024&onward=14-Aug-2024'}, {'bus_name': 'KSRTC (Kerala) - 2518', 'bus_type': 'Swift Deluxe Non AC Air Bus (2+2)', 'departure_time': '00:11', 'duration': '04h 43m', 'reaching_time': '04:54', 'star_rating': '3.0', 'price': 'INR 309', 'seat_availability': '31 Seats available', 'route_name': 'Kozhikode to Ernakulam Bus', 'route_link': 'https://www.redbus.in/bus-tickets/kozhikode-to-ernakulam?fr

In [13]:
# Converting into DATAFRAME 

df_kerala_details=pd.DataFrame(bus_details)
df_kerala_details

bus_name                                   bus_type  \
0     KSRTC (Kerala) - 1029             Super Fast Non AC Seater (2+3)   
1     KSRTC (Kerala) - 2518          Swift Deluxe Non AC Air Bus (2+2)   
2     KSRTC (Kerala) - 2072  Super Express Non AC Seater Air Bus (2+2)   
3     KSRTC (Kerala) - 2368                    Low Floor AC Seater 2+2   
4      KSRTC (Kerala) - 698             Super Fast Non AC Seater (2+3)   
...                     ...                                        ...   
1096  Ravina Travels (Regd)                          A/C Sleeper (2+1)   
1097         Cochin Express                 A/C Seater Push Back (2+2)   
1098         Cochin Express                 A/C Seater Push Back (2+2)   
1099          Sonia Travels                   A/C Seater/Sleeper (2+1)   
1100          Sonia Travels                   A/C Seater/Sleeper (2+1)   

     departure_time duration reaching_time star_rating     price  \
0             00:00  05h 35m         05:35         3.0   INR 269   
1             00:11  04h 43m         04:54         3.0   INR 309   
2             00:30  04h 20m         04:50      2.9\n5   INR 268   
3             00:30  05h 19m         05:49      2.4\n6   INR 383   
4             00:45  04h 54m         05:39      1.8\n8   INR 230   
...             ...      ...           ...         ...       ...   
1096          10:40  02h 20m         13:00         3.0  INR 1399   
1097          22:30  01h 25m         23:55         4.1   INR 700   
1098          22:30  01h 25m         23:55         4.1   INR 700   
1099          19:30  03h 59m         23:29         3.8   INR 750   
1100          21:30  01h 59m         23:29         3.8   INR 750   

       seat_availability                          route_name  \
0     49 Seats available          Kozhikode to Ernakulam Bus   
1     31 Seats available          Kozhikode to Ernakulam Bus   
2     22 Seats available          Kozhikode to Ernakulam Bus   
3     15 Seats available          Kozhikode to Ernakulam Bus   
4     44 Seats available          Kozhikode to Ernakulam Bus   
...                  ...                                 ...   
1096  24 Seats available  Kalpetta (kerala) to Kozhikode Bus   
1097  41 Seats available  Kalpetta (kerala) to Kozhikode Bus   
1098  41 Seats available  Kalpetta (kerala) to Kozhikode Bus   
1099  40 Seats available  Kalpetta (kerala) to Kozhikode Bus   
1100  40 Seats available  Kalpetta (kerala) to Kozhikode Bus   

                                             route_link  
0     https://www.redbus.in/bus-tickets/kozhikode-to...  
1     https://www.redbus.in/bus-tickets/kozhikode-to...  
2     https://www.redbus.in/bus-tickets/kozhikode-to...  
3     https://www.redbus.in/bus-tickets/kozhikode-to...  
4     https://www.redbus.in/bus-tickets/kozhikode-to...  
...                                                 ...  
1096  https://www.redbus.in/bus-tickets/kalpetta-to-...  
1097  https://www.redbus.in/bus-tickets/kalpetta-to-...  
1098  https://www.redbus.in/bus-tickets/kalpetta-to-...  
1099  https://www.redbus.in/bus-tickets/kalpetta-to-...  
1100  https://www.redbus.in/bus-tickets/kalpetta-to-...  

[1101 rows x 10 columns]

In [ ]:
#printing length, head ,tail
print(len(df_kerala_details))
print(df_kerala_details.head())
print(df_kerala_details.tail())


In [23]:
#change dataframe to csv

df_kerala_details.to_csv('kerala_buses.csv', index=False)

TSRTC BUS Details

In [16]:
#read csv file
df=pd.read_csv("tsrtc_routes.csv")
df

Route name  \
0                      Khammam to Hyderabad   
1                   Hyderabad to Vijayawada   
2                      Hyderabad to Khammam   
3                    Hyderabad to Srisailam   
4                   Karimnagar to Hyderabad   
5                       Hyderabad to Nirmal   
6                   Hyderabad to Mancherial   
7                     Hyderabad to Adilabad   
8                   Hyderabad to Karimnagar   
9                   Kothagudem to Hyderabad   
10     Guntur (Andhra Pradesh) to Hyderabad   
11               Godavarikhani to Hyderabad   
12                       Kodad to Hyderabad   
13                Hyderabad to Bhadrachalam   
14                  Hyderabad to Kothagudem   
15                    Jagityal to Hyderabad   
16                     Hyderabad to Kurnool   
17                  Hyderabad to Sathupally   
18                      Hyderabad to Armoor   
19               Hyderabad to Godavarikhani   
20  Hyderabad to Anantapur (andhra pradesh)   
21                    Hyderabad to Warangal   
22                      Hyderabad to Ongole   
23     Hyderabad to Guntur (Andhra Pradesh)   
24                      Kadapa to Hyderabad   
25                    Hyderabad to Tirupati   

                                           Route link  
0   https://www.redbus.in/bus-tickets/khammam-to-h...  
1   https://www.redbus.in/bus-tickets/hyderabad-to...  
2   https://www.redbus.in/bus-tickets/hyderabad-to...  
3   https://www.redbus.in/bus-tickets/hyderabad-to...  
4   https://www.redbus.in/bus-tickets/karimnagar-t...  
5   https://www.redbus.in/bus-tickets/hyderabad-to...  
6   https://www.redbus.in/bus-tickets/hyderabad-to...  
7   https://www.redbus.in/bus-tickets/hyderabad-to...  
8   https://www.redbus.in/bus-tickets/hyderabad-to...  
9   https://www.redbus.in/bus-tickets/kothagudem-t...  
10  https://www.redbus.in/bus-tickets/guntur-to-hy...  
11  https://www.redbus.in/bus-tickets/godavarikhan...  
12  https://www.redbus.in/bus-tickets/kodad-to-hyd...  
13  https://www.redbus.in/bus-tickets/hyderabad-to...  
14  https://www.redbus.in/bus-tickets/hyderabad-to...  
15  https://www.redbus.in/bus-tickets/jagityal-to-...  
16  https://www.redbus.in/bus-tickets/hyderabad-to...  
17  https://www.redbus.in/bus-tickets/hyderabad-to...  
18  https://www.redbus.in/bus-tickets/hyderabad-to...  
19  https://www.redbus.in/bus-tickets/hyderabad-to...  
20  https://www.redbus.in/bus-tickets/hyderabad-to...  
21  https://www.redbus.in/bus-tickets/hyderabad-to...  
22  https://www.redbus.in/bus-tickets/hyderabad-to...  
23  https://www.redbus.in/bus-tickets/hyderabad-to...  
24  https://www.redbus.in/bus-tickets/kadapa-to-hy...  
25  https://www.redbus.in/bus-tickets/hyderabad-to...

In [18]:
driver = webdriver.Chrome()

#Creating a list to store bus details

bus_details = []

#looping the each route links in the  dataframe :

for i in df["Route link"]:

    driver.get(i) #

    full_url = driver.current_url
    driver.get(full_url + f'&onward=14-Aug-2024')

    time.sleep(2)  # Let the page load
    driver.maximize_window()
    
    # To get route name and route links
    try:
        route_name = driver.find_element(By.CLASS_NAME, 'D136_h1').text
        route_link = driver.current_url
    except Exception as e:
        print(f"Error retrieving route name or link: {e}")
        continue
    
    # Initialize WebDriverWait
    wait = WebDriverWait(driver, 20)  # Increased timeout

    # Wait for buttons to be visible and click them
    try:
        govt_buttons = wait.until(EC.visibility_of_all_elements_located((By.XPATH, './/div[@class="button"]')))
        for govt_button in govt_buttons[::-1]:
                driver.execute_script("window.scrollTo(0, 330);")
                govt_button.click()
                time.sleep(2)
                
    except Exception as e:
        print(f"Error waiting for buttons: {e}")
        continue

    # Scroll down to load more buses
    scroll_to_load(driver, 10)

    # Wait until all  bus items  present
    try:
        wait.until(EC.presence_of_all_elements_located((By.CLASS_NAME, 'bus-item')))
        containers = driver.find_elements(By.CLASS_NAME, 'bus-item')
        for container in containers:
            try:
                bus_names = container.find_element(By.XPATH, './/div[@class="travels lh-24 f-bold d-color"]').text
                bus_type = container.find_element(By.XPATH, './/div[@class="bus-type f-12 m-top-16 l-color evBus"]').text
                departure_time = container.find_element(By.XPATH, './/div[@class="dp-time f-19 d-color f-bold"]').text
                duration = container.find_element(By.XPATH, './/div[@class="dur l-color lh-24"]').text
                reaching_time = container.find_element(By.XPATH, './/div[@class="bp-time f-19 d-color disp-Inline"]').text
                star_rating = container.find_element(By.XPATH,".//div[@class='column-six p-right-10 w-10 fl']").text
                price = container.find_element(By.XPATH, './/div[@class="fare d-block"]').text
                seat_availability = container.find_element(By.XPATH, './/div[contains(@class,"seat-left")]').text

                 
                bus_details.append({
                    "bus_name": bus_names,
                    "bus_type": bus_type,
                    "departure_time": departure_time,
                    "duration": duration,
                    "reaching_time": reaching_time,
                    "star_rating": star_rating,
                    "price": price,
                    "seat_availability": seat_availability,
                    "route_name": route_name,
                    "route_link": route_link
                })
            except Exception as e:
                print(f"Error extracting details: {e}")
    except Exception as e:
        print(f"Error waiting for bus items: {e}")

    

# Print the collected bus details
print(bus_details)



Error waiting for buttons: Message: 

[{'bus_name': 'TSRTC - 8987', 'bus_type': 'SUPER LUXURY (NON-AC, 2 + 2 PUSH BACK)', 'departure_time': '00:25', 'duration': '03h 55m', 'reaching_time': '04:20', 'star_rating': '3.7\n32', 'price': 'INR 320', 'seat_availability': '28 Seats available', 'route_name': 'Khammam to Hyderabad Bus', 'route_link': 'https://www.redbus.in/bus-tickets/khammam-to-hyderabad?fromCityId=401&toCityId=124&fromCityName=Khammam&toCityName=Hyderabad&busType=Any&srcCountry=IND&destCountry=IND&onward=12-Aug-2024&onward=14-Aug-2024'}, {'bus_name': 'TSRTC - 8885', 'bus_type': 'Lahari Non A/C Sleeper Cum Seater', 'departure_time': '01:15', 'duration': '04h 00m', 'reaching_time': '05:15', 'star_rating': '4.8\n32', 'price': 'INR 320', 'seat_availability': '36 Seats available', 'route_name': 'Khammam to Hyderabad Bus', 'route_link': 'https://www.redbus.in/bus-tickets/khammam-to-hyderabad?fromCityId=401&toCityId=124&fromCityName=Khammam&toCityName=Hyderabad&busType=Any&srcCountry

In [19]:
# Converting into DATAFRAME 

df_tsrtc_details=pd.DataFrame(bus_details)
df_tsrtc_details

bus_name  \
0                           TSRTC - 8987   
1                           TSRTC - 8885   
2                           TSRTC - 8949   
3                           TSRTC - 8653   
4                           TSRTC - 8631   
...                                  ...   
2482                Mahi Trans Solutions   
2483                          RK Travels   
2484              SRI RATAN TATA EXPRESS   
2485                            True Bus   
2486  Elegance Tours And Travels Pvt Ltd   

                                     bus_type departure_time     duration  \
0      SUPER LUXURY (NON-AC, 2 + 2 PUSH BACK)          00:25      03h 55m   
1           Lahari Non A/C Sleeper Cum Seater          01:15      04h 00m   
2                RAJDHANI (A.C. Semi Sleeper)          01:15      03h 55m   
3       RAJADHANI AC (CONVERTED METRO LUXURY)          03:00      04h 00m   
4       RAJADHANI AC (CONVERTED METRO LUXURY)          03:30      04h 00m   
...                                       ...            ...          ...   
2482                        A/C Sleeper (2+1)          20:00      11h 15m   
2483           Non A/C Seater / Sleeper (2+1)          21:00  0-12h 0-30m   
2484                        A/C Sleeper (2+1)          23:45      09h 45m   
2485  A/C Volvo B11R Multi-Axle Sleeper (2+1)          19:00      11h 00m   
2486            Bharat Benz A/C Sleeper (2+1)          19:00      11h 00m   

     reaching_time star_rating     price   seat_availability  \
0            04:20     3.7\n32   INR 320  28 Seats available   
1            05:15     4.8\n32   INR 320  36 Seats available   
2            05:10         3.7   INR 389  35 Seats available   
3            07:00     4.3\n65   INR 389  34 Seats available   
4            07:30     3.6\n82   INR 389  34 Seats available   
...            ...         ...       ...                 ...   
2482         07:15         3.7  INR 2499    1 Seat available   
2483         09:30         3.5  INR 5000  36 Seats available   
2484         09:30         3.5      2564  24 Seats available   
2485         06:00         3.5  INR 2299  27 Seats available   
2486         06:00         1.9  INR 1550  27 Seats available   

                     route_name  \
0      Khammam to Hyderabad Bus   
1      Khammam to Hyderabad Bus   
2      Khammam to Hyderabad Bus   
3      Khammam to Hyderabad Bus   
4      Khammam to Hyderabad Bus   
...                         ...   
2482  Hyderabad to Tirupati Bus   
2483  Hyderabad to Tirupati Bus   
2484  Hyderabad to Tirupati Bus   
2485  Hyderabad to Tirupati Bus   
2486  Hyderabad to Tirupati Bus   

                                             route_link  
0     https://www.redbus.in/bus-tickets/khammam-to-h...  
1     https://www.redbus.in/bus-tickets/khammam-to-h...  
2     https://www.redbus.in/bus-tickets/khammam-to-h...  
3     https://www.redbus.in/bus-tickets/khammam-to-h...  
4     https://www.redbus.in/bus-tickets/khammam-to-h...  
...                                                 ...  
2482  https://www.redbus.in/bus-tickets/hyderabad-to...  
2483  https://www.redbus.in/bus-tickets/hyderabad-to...  
2484  https://www.redbus.in/bus-tickets/hyderabad-to...  
2485  https://www.redbus.in/bus-tickets/hyderabad-to...  
2486  https://www.redbus.in/bus-tickets/hyderabad-to...  

[2487 rows x 10 columns]

In [ ]:
#printing length, head ,tail
print(len(df_tsrtc_details))
print(df_tsrtc_details.head())
print(df_tsrtc_details.tail())

In [22]:
#change dataframe to csv

df_tsrtc_details.to_csv('tsrtc_buses.csv', index=False)

APSRTC BUSES DETAILS

In [24]:
#read csv file
df=pd.read_csv("apsrtc_routes.csv")
df

Route name  \
0                   Vijayawada to Hyderabad   
1                   Hyderabad to Vijayawada   
2                 Kakinada to Visakhapatnam   
3                 Visakhapatnam to Kakinada   
4    Chittoor (Andhra Pradesh) to Bangalore   
5                       Kadapa to Bangalore   
6   Anantapur (andhra pradesh) to Bangalore   
7                     Tirupati to Bangalore   
8               Visakhapatnam to Vijayawada   
9                       Ongole to Hyderabad   
10                    Bangalore to Tirupati   
11   Macherla (andhra pradesh) to Hyderabad   
12             Rajahmundry to Visakhapatnam   
13                     Nandyal to Hyderabad   
14                      Bangalore to Kadapa   
15                      Hyderabad to Ongole   
16     Guntur (Andhra Pradesh) to Hyderabad   
17              Vijayawada to Visakhapatnam   
18                Rajahmundry to Vijayawada   
19                     Hyderabad to Kurnool   
20   Bangalore to Chittoor (Andhra Pradesh)   
21                     Kurnool to Hyderabad   
22             Visakhapatnam to Rajahmundry   
23                   Rayachoti to Bangalore   
24                   Vinukonda to Hyderabad   
25  Bangalore to Anantapur (andhra pradesh)   
26              Amalapuram to Visakhapatnam   
27                   Vijayawada to Tirupati   
28                 Madanapalli to Bangalore   
29                Narasaraopet to Hyderabad   
30                       Eluru to Hyderabad   
31              Visakhapatnam to Amalapuram   
32                      Kadiri to Bangalore   
33                      Chennai to Tirupati   
34                 Rajahmundry to Hyderabad   
35                    Kurnool to Vijayawada   
36                    Vijayawada to Kurnool   
37                   Kakinada to Vijayawada   
38                 Bangalore to Madanapalli   
39                     Nellore to Bangalore   
40                Hyderabad to Narasaraopet   
41     Hyderabad to Guntur (Andhra Pradesh)   
42                      Bangalore to Kadiri   
43                Vijayawada to Rajahmundry   
44                   Bangalore to Rayachoti   
45                     Kurnool to Bangalore   
46                      Tirupati to Chennai   
47  Hyderabad to Anantapur (andhra pradesh)   
48  Anantapur (andhra pradesh) to Hyderabad   

                                           Route link  
0   https://www.redbus.in/bus-tickets/vijayawada-t...  
1   https://www.redbus.in/bus-tickets/hyderabad-to...  
2   https://www.redbus.in/bus-tickets/kakinada-to-...  
3   https://www.redbus.in/bus-tickets/visakhapatna...  
4   https://www.redbus.in/bus-tickets/chittoor-and...  
5   https://www.redbus.in/bus-tickets/kadapa-to-ba...  
6   https://www.redbus.in/bus-tickets/ananthapur-t...  
7   https://www.redbus.in/bus-tickets/tirupathi-to...  
8   https://www.redbus.in/bus-tickets/visakhapatna...  
9   https://www.redbus.in/bus-tickets/ongole-to-hy...  
10  https://www.redbus.in/bus-tickets/bangalore-to...  
11  https://www.redbus.in/bus-tickets/macherla-to-...  
12  https://www.redbus.in/bus-tickets/rajahmundry-...  
13  https://www.redbus.in/bus-tickets/nandyala-to-...  
14  https://www.redbus.in/bus-tickets/bangalore-to...  
15  https://www.redbus.in/bus-tickets/hyderabad-to...  
16  https://www.redbus.in/bus-tickets/guntur-to-hy...  
17  https://www.redbus.in/bus-tickets/vijayawada-t...  
18  https://www.redbus.in/bus-tickets/rajahmundry-...  
19  https://www.redbus.in/bus-tickets/hyderabad-to...  
20  https://www.redbus.in/bus-tickets/bangalore-to...  
21  https://www.redbus.in/bus-tickets/kurnool-to-h...  
22  https://www.redbus.in/bus-tickets/visakhapatna...  
23  https://www.redbus.in/bus-tickets/rayachoti-to...  
24  https://www.redbus.in/bus-tickets/vinukonda-to...  
25  https://www.redbus.in/bus-tickets/bangalore-to...  
26  https://www.redbus.in/bus-tickets/amalapuram-t...  
27  https://www.redbus.in/bus-tickets/vijayawada-t...  
28  https://www.redbus.in/bus-tickets/madanapalli-...  
29

In [25]:
driver = webdriver.Chrome()

#Creating a list to store bus details

bus_details = []

#looping the each route links in the  dataframe :

for i in df["Route link"]:

    driver.get(i) #

    full_url = driver.current_url
    driver.get(full_url + f'&onward=14-Aug-2024')

    time.sleep(2)  # Let the page load
    driver.maximize_window()
    
    # To get route name and route links
    try:
        route_name = driver.find_element(By.CLASS_NAME, 'D136_h1').text
        route_link = driver.current_url
    except Exception as e:
        print(f"Error retrieving route name or link: {e}")
        continue
    
    # Initialize WebDriverWait
    wait = WebDriverWait(driver, 20)  # Increased timeout

    # Wait for buttons to be visible and click them
    try:
        govt_buttons = wait.until(EC.visibility_of_all_elements_located((By.XPATH, './/div[@class="button"]')))
        for govt_button in govt_buttons[::-1]:
                driver.execute_script("window.scrollTo(0, 330);")
                govt_button.click()
                time.sleep(2)
                
    except Exception as e:
        print(f"Error waiting for buttons: {e}")
        continue

    # Scroll down to load more buses
    scroll_to_load(driver, 10)

    # Wait until all  bus items  present
    try:
        wait.until(EC.presence_of_all_elements_located((By.CLASS_NAME, 'bus-item')))
        containers = driver.find_elements(By.CLASS_NAME, 'bus-item')
        for container in containers:
            try:
                bus_names = container.find_element(By.XPATH, './/div[@class="travels lh-24 f-bold d-color"]').text
                bus_type = container.find_element(By.XPATH, './/div[@class="bus-type f-12 m-top-16 l-color evBus"]').text
                departure_time = container.find_element(By.XPATH, './/div[@class="dp-time f-19 d-color f-bold"]').text
                duration = container.find_element(By.XPATH, './/div[@class="dur l-color lh-24"]').text
                reaching_time = container.find_element(By.XPATH, './/div[@class="bp-time f-19 d-color disp-Inline"]').text
                star_rating = container.find_element(By.XPATH,".//div[@class='column-six p-right-10 w-10 fl']").text
                price = container.find_element(By.XPATH, './/div[@class="fare d-block"]').text
                seat_availability = container.find_element(By.XPATH, './/div[contains(@class,"seat-left")]').text

                 
                bus_details.append({
                    "bus_name": bus_names,
                    "bus_type": bus_type,
                    "departure_time": departure_time,
                    "duration": duration,
                    "reaching_time": reaching_time,
                    "star_rating": star_rating,
                    "price": price,
                    "seat_availability": seat_availability,
                    "route_name": route_name,
                    "route_link": route_link
                })
            except Exception as e:
                print(f"Error extracting details: {e}")
    except Exception as e:
        print(f"Error waiting for bus items: {e}")

    

# Print the collected bus details
print(bus_details)



Error waiting for buttons: Message: 

[{'bus_name': 'APSRTC - 2673', 'bus_type': 'Super Luxury (Non AC Seater 2+2 Push Back)', 'departure_time': '00:15', 'duration': '04h 55m', 'reaching_time': '05:10', 'star_rating': '2.6\n15', 'price': 'INR 469', 'seat_availability': '33 Seats available', 'route_name': 'Vijayawada to Hyderabad Bus', 'route_link': 'https://www.redbus.in/bus-tickets/vijayawada-to-hyderabad?fromCityId=134&toCityId=124&fromCityName=Vijayawada&toCityName=Hyderabad&busType=Any&srcCountry=IND&destCountry=IND&onward=12-Aug-2024&onward=14-Aug-2024'}, {'bus_name': 'APSRTC - 37800', 'bus_type': 'INDRA(A.C. Seater)', 'departure_time': '00:15', 'duration': '05h 30m', 'reaching_time': '05:45', 'star_rating': '2.7\n4', 'price': 'INR 567', 'seat_availability': '34 Seats available', 'route_name': 'Vijayawada to Hyderabad Bus', 'route_link': 'https://www.redbus.in/bus-tickets/vijayawada-to-hyderabad?fromCityId=134&toCityId=124&fromCityName=Vijayawada&toCityName=Hyderabad&busType=Any&s

In [29]:
# Converting into DATAFRAME 

df_apsrtc_details=pd.DataFrame(bus_details)
df_apsrtc_details

bus_name                                    bus_type  \
0          APSRTC - 2673  Super Luxury (Non AC Seater 2+2 Push Back)   
1         APSRTC - 37800                          INDRA(A.C. Seater)   
2         APSRTC - 24255                          INDRA(A.C. Seater)   
3          APSRTC - 2572  AMARAVATHI (VOLVO / SCANIA A.C Multi Axle)   
4          APSRTC - 2562                          INDRA(A.C. Seater)   
...                  ...                                         ...   
6278  DHANUNJAYA TRAVELS            A/C Semi Sleeper / Sleeper (2+1)   
6279  DHANUNJAYA TRAVELS                  A/C Seater / Sleeper (2+1)   
6280  DHANUNJAYA TRAVELS                           A/C Sleeper (2+1)   
6281    Northern Travels       Bharat Benz A/C Seater /Sleeper (2+1)   
6282    Northern Travels       Bharat Benz A/C Seater /Sleeper (2+1)   

     departure_time duration reaching_time star_rating     price  \
0             00:15  04h 55m         05:10     2.6\n15   INR 469   
1             00:15  05h 30m         05:45      2.7\n4   INR 567   
2             00:20  04h 20m         04:40      1.5\n4   INR 528   
3             00:30  05h 55m         06:25     5.0\n16   INR 720   
4             00:40  04h 40m         05:20         4.0   INR 528   
...             ...      ...           ...         ...       ...   
6278          14:00  06h 00m         20:00         2.8  INR 1099   
6279          14:00  07h 00m         21:00         2.8  INR 1299   
6280          01:25  06h 00m         07:25         2.8  INR 1990   
6281          01:20  05h 45m         07:05         2.0      1568   
6282          01:45  06h 10m         07:55         2.0      1424   

       seat_availability                                   route_name  \
0     33 Seats available                  Vijayawada to Hyderabad Bus   
1     34 Seats available                  Vijayawada to Hyderabad Bus   
2     38 Seats available                  Vijayawada to Hyderabad Bus   
3     34 Seats available                  Vijayawada to Hyderabad Bus   
4     38 Seats available                  Vijayawada to Hyderabad Bus   
...                  ...                                          ...   
6278  28 Seats available  Anantapur (andhra pradesh) to Hyderabad Bus   
6279  32 Seats available  Anantapur (andhra pradesh) to Hyderabad Bus   
6280  24 Seats available  Anantapur (andhra pradesh) to Hyderabad Bus   
6281  40 Seats available  Anantapur (andhra pradesh) to Hyderabad Bus   
6282  40 Seats available  Anantapur (andhra pradesh) to Hyderabad Bus   

                                             route_link  
0     https://www.redbus.in/bus-tickets/vijayawada-t...  
1     https://www.redbus.in/bus-tickets/vijayawada-t...  
2     https://www.redbus.in/bus-tickets/vijayawada-t...  
3     https://www.redbus.in/bus-tickets/vijayawada-t...  
4     https://www.redbus.in/bus-tickets/vijayawada-t...  
...                                                 ...  
6278  https://www.redbus.in/bus-tickets/ananthapur-t...  
6279  https://www.redbus.in/bus-tickets/ananthapur-t...  
6280  https://www.redbus.in/bus-tickets/ananthapur-t...  
6281  https://www.redbus.in/bus-tickets/ananthapur-t...  
6282  https://www.redbus.in/bus-tickets/ananthapur-t...  

[6283 rows x 10 columns]

In [27]:
#change dataframe to csv

df_apsrtc_details.to_csv('apsrtc_buses.csv', index=False)

RSRTC BUS DETAILS

In [30]:
#read csv file
df=pd.read_csv("rsrtc_routes.csv")
df

Route name  \
0                                Jodhpur to Ajmer   
1        Beawar (Rajasthan) to Jaipur (Rajasthan)   
2                              Udaipur to Jodhpur   
3                   Jaipur (Rajasthan) to Jodhpur   
4                     Sikar to Jaipur (Rajasthan)   
5                Kishangarh to Jaipur (Rajasthan)   
6   Aligarh (uttar pradesh) to Jaipur (Rajasthan)   
7                   Jodhpur to Beawar (Rajasthan)   
8           Kota(Rajasthan) to Jaipur (Rajasthan)   
9   Jaipur (Rajasthan) to Aligarh (uttar pradesh)   
10          Jaipur (Rajasthan) to Kota(Rajasthan)   
11                    Pali (Rajasthan) to Udaipur   
12                    Udaipur to Pali (Rajasthan)   
13                               Sikar to Bikaner   
14                Jaipur (Rajasthan) to Bharatpur   
15                          Kishangarh to Jodhpur   
16                 Jaipur (Rajasthan) to Bhilwara   
17                     Kota(Rajasthan) to Udaipur   
18                   Jaipur (Rajasthan) to Pilani   
19                  Jaipur (Rajasthan) to Mathura   
20                               Bikaner to Sikar   

                                           Route link  
0   https://www.redbus.in/bus-tickets/jodhpur-to-a...  
1   https://www.redbus.in/bus-tickets/beawer-to-ja...  
2   https://www.redbus.in/bus-tickets/udaipur-to-j...  
3   https://www.redbus.in/bus-tickets/jaipur-to-jo...  
4   https://www.redbus.in/bus-tickets/sikar-to-jaipur  
5   https://www.redbus.in/bus-tickets/kishangarh-t...  
6   https://www.redbus.in/bus-tickets/aligarh-utta...  
7   https://www.redbus.in/bus-tickets/jodhpur-to-b...  
8   https://www.redbus.in/bus-tickets/kota-rajasth...  
9   https://www.redbus.in/bus-tickets/jaipur-to-al...  
10  https://www.redbus.in/bus-tickets/jaipur-to-ko...  
11  https://www.redbus.in/bus-tickets/pali-to-udaipur  
12  https://www.redbus.in/bus-tickets/udaipur-to-p...  
13  https://www.redbus.in/bus-tickets/sikar-to-bik...  
14  https://www.redbus.in/bus-tickets/jaipur-to-bh...  
15  https://www.redbus.in/bus-tickets/kishangarh-t...  
16  https://www.redbus.in/bus-tickets/jaipur-to-bh...  
17  https://www.redbus.in/bus-tickets/kota-rajasth...  
18  https://www.redbus.in/bus-tickets/jaipur-to-pi...  
19  https://www.redbus.in/bus-tickets/jaipur-to-ma...  
20  https://www.redbus.in/bus-tickets/bikaner-to-s...

In [32]:
driver = webdriver.Chrome()

#Creating a list to store bus details

bus_details = []

#looping the each route links in the  dataframe :

for i in df["Route link"]:

    driver.get(i) #

    full_url = driver.current_url
    driver.get(full_url + f'&onward=14-Aug-2024')

    time.sleep(2)  # Let the page load
    driver.maximize_window()
    
    # To get route name and route links
    try:
        route_name = driver.find_element(By.CLASS_NAME, 'D136_h1').text
        route_link = driver.current_url
    except Exception as e:
        print(f"Error retrieving route name or link: {e}")
        continue
    
    # Initialize WebDriverWait
    wait = WebDriverWait(driver, 20)  # Increased timeout

    # Wait for buttons to be visible and click them
    try:
        govt_buttons = wait.until(EC.visibility_of_all_elements_located((By.XPATH, './/div[@class="button"]')))
        for govt_button in govt_buttons[::-1]:
                driver.execute_script("window.scrollTo(0, 330);")
                govt_button.click()
                time.sleep(2)
                
    except Exception as e:
        print(f"Error waiting for buttons: {e}")
        continue

    # Scroll down to load more buses
    scroll_to_load(driver, 10)

    # Wait until all  bus items  present
    try:
        wait.until(EC.presence_of_all_elements_located((By.CLASS_NAME, 'bus-item')))
        containers = driver.find_elements(By.CLASS_NAME, 'bus-item')
        for container in containers:
            try:
                bus_names = container.find_element(By.XPATH, './/div[@class="travels lh-24 f-bold d-color"]').text
                bus_type = container.find_element(By.XPATH, './/div[@class="bus-type f-12 m-top-16 l-color evBus"]').text
                departure_time = container.find_element(By.XPATH, './/div[@class="dp-time f-19 d-color f-bold"]').text
                duration = container.find_element(By.XPATH, './/div[@class="dur l-color lh-24"]').text
                reaching_time = container.find_element(By.XPATH, './/div[@class="bp-time f-19 d-color disp-Inline"]').text
                star_rating = container.find_element(By.XPATH,".//div[@class='column-six p-right-10 w-10 fl']").text
                price = container.find_element(By.XPATH, './/div[@class="fare d-block"]').text
                seat_availability = container.find_element(By.XPATH, './/div[contains(@class,"seat-left")]').text

                 
                bus_details.append({
                    "bus_name": bus_names,
                    "bus_type": bus_type,
                    "departure_time": departure_time,
                    "duration": duration,
                    "reaching_time": reaching_time,
                    "star_rating": star_rating,
                    "price": price,
                    "seat_availability": seat_availability,
                    "route_name": route_name,
                    "route_link": route_link
                })
            except Exception as e:
                print(f"Error extracting details: {e}")
    except Exception as e:
        print(f"Error waiting for bus items: {e}")

    

# Print the collected bus details
print(bus_details)



[{'bus_name': 'RSRTC - 160781', 'bus_type': 'Super Luxury Volvo AC Seater Pushback 2+2', 'departure_time': '00:00', 'duration': '14h 00m', 'reaching_time': '14:00', 'star_rating': '4.6\n6', 'price': 'INR 460', 'seat_availability': '37 Seats available', 'route_name': 'Jodhpur to Ajmer Bus', 'route_link': 'https://www.redbus.in/bus-tickets/jodhpur-to-ajmer?fromCityId=1169&toCityId=808&fromCityName=Jodhpur&toCityName=Ajmer&busType=Any&onward=14-Aug-2024&onward=14-Aug-2024'}, {'bus_name': 'RSRTC - 192566', 'bus_type': 'Semi Deluxe Non AC Seater 2+2', 'departure_time': '04:45', 'duration': '04h 30m', 'reaching_time': '09:15', 'star_rating': '4.2', 'price': 'INR 250', 'seat_availability': '35 Seats available', 'route_name': 'Jodhpur to Ajmer Bus', 'route_link': 'https://www.redbus.in/bus-tickets/jodhpur-to-ajmer?fromCityId=1169&toCityId=808&fromCityName=Jodhpur&toCityName=Ajmer&busType=Any&onward=14-Aug-2024&onward=14-Aug-2024'}, {'bus_name': 'RSRTC - 146314', 'bus_type': 'Super Luxury Volvo

In [33]:
# Converting into DATAFRAME 

df_rsrtc_details=pd.DataFrame(bus_details)
df_rsrtc_details

bus_name                                   bus_type  \
0             RSRTC - 160781  Super Luxury Volvo AC Seater Pushback 2+2   
1             RSRTC - 192566              Semi Deluxe Non AC Seater 2+2   
2             RSRTC - 146314  Super Luxury Volvo AC Seater Pushback 2+2   
3             RSRTC - 193343              Semi Deluxe Non AC Seater 2+2   
4             RSRTC - 185141  Super Luxury Volvo AC Seater Pushback 2+2   
...                      ...                                        ...   
1863          Sharma travels                 A/C Seater / Sleeper (2+1)   
1864    Amar Travels(Jaipur)                 A/C Seater / Sleeper (2+1)   
1865  RATHORE TRAVELS AGENCY               Volvo 9600 A/C Sleeper (2+1)   
1866             M R Travels  Volvo Multi-Axle A/C seater/sleeper (2+1)   
1867  RATHORE TRAVELS AGENCY               Volvo 9600 A/C Sleeper (2+1)   

     departure_time duration reaching_time star_rating     price  \
0             00:00  14h 00m         14:00      4.6\n6   INR 460   
1             04:45  04h 30m         09:15         4.2   INR 250   
2             06:15  04h 00m         10:15     4.3\n60   INR 460   
3             07:15  04h 45m         12:00         4.2   INR 250   
4             07:15  04h 00m         11:15     4.3\n47   INR 460   
...             ...      ...           ...         ...       ...   
1863          22:30  04h 30m         03:00         1.9   INR 429   
1864          22:45  04h 45m         03:30         2.4   INR 400   
1865          14:40  03h 12m         17:52      5.0\n4   INR 850   
1866          15:15  03h 00m         18:15         3.8  INR 4000   
1867          23:00  04h 15m         03:15         4.1   INR 850   

       seat_availability            route_name  \
0     37 Seats available  Jodhpur to Ajmer Bus   
1     35 Seats available  Jodhpur to Ajmer Bus   
2     36 Seats available  Jodhpur to Ajmer Bus   
3     35 Seats available  Jodhpur to Ajmer Bus   
4     37 Seats available  Jodhpur to Ajmer Bus   
...                  ...                   ...   
1863  34 Seats available  Bikaner to Sikar Bus   
1864  44 Seats available  Bikaner to Sikar Bus   
1865  36 Seats available  Bikaner to Sikar Bus   
1866  60 Seats available  Bikaner to Sikar Bus   
1867  36 Seats available  Bikaner to Sikar Bus   

                                             route_link  
0     https://www.redbus.in/bus-tickets/jodhpur-to-a...  
1     https://www.redbus.in/bus-tickets/jodhpur-to-a...  
2     https://www.redbus.in/bus-tickets/jodhpur-to-a...  
3     https://www.redbus.in/bus-tickets/jodhpur-to-a...  
4     https://www.redbus.in/bus-tickets/jodhpur-to-a...  
...                                                 ...  
1863  https://www.redbus.in/bus-tickets/bikaner-to-s...  
1864  https://www.redbus.in/bus-tickets/bikaner-to-s...  
1865  https://www.redbus.in/bus-tickets/bikaner-to-s...  
1866  https://www.redbus.in/bus-tickets/bikaner-to-s...  
1867  https://www.redbus.in/bus-tickets/bikaner-to-s...  

[1868 rows x 10 columns]

In [34]:
#change dataframe to csv

df_rsrtc_details.to_csv('rsrtc_buses.csv', index=False)

South Bengal State Transport Corporation (SBSTC) BUS DETAILS

In [35]:
#read csv file
df=pd.read_csv("sbstc_routes.csv")
df

Route name  \
0                                  Burdwan to Kolkata   
1                                  Kolkata to Burdwan   
2                   Durgapur (West Bengal) to Kolkata   
3                                   Kolkata to Haldia   
4                                   Haldia to Kolkata   
5                   Kolkata to Durgapur (West Bengal)   
6                   Kolkata to Arambagh (West Bengal)   
7                                    Digha to Kolkata   
8                                    Kolkata to Digha   
9                                  Kolkata to Bankura   
10                   Asansol (West Bengal) to Kolkata   
11                               Midnapore to Kolkata   
12                   Kolkata to Asansol (West Bengal)   
13                                Kolkata to Siliguri   
14                                Kolkata to Nimtouri   
15                                Siliguri to Kolkata   
16                         Kolkata to Contai (Kanthi)   
17                    Digha to Durgapur (West Bengal)   
18                               Kolkata to Midnapore   
19                Kolkata to Nandakumar (west bengal)   
20                   Kolkata to Mecheda (West Bengal)   
21                    Durgapur (West Bengal) to Digha   
22                                Kolkata to Kolaghat   
23                                Jhargram to Kolkata   
24                     Digha to Barasat (West Bengal)   
25                 Durgapur (West Bengal) to Siliguri   
26                 Midnapore to Barasat (West Bengal)   
27                                   Kolkata to Heria   
28                 Kolkata to Chandipur (West Bengal)   
29                 Siliguri to Durgapur (West Bengal)   
30  Berhampore (West Bengal) to Durgapur (West Ben...   
31                   Berhampore (West Bengal) to Suri   
32                     Barasat (West Bengal) to Digha   
33                              Kolkata to Futishanko   
34                 Barasat (West Bengal) to Midnapore   
35  Durgapur (West Bengal) to Berhampore (West Ben...   
36                    Durgapur (West Bengal) to Malda   
37                     Digha to Asansol (West Bengal)   
38                  Kolkata to Ramnagar (West Bengal)   
39                    Kolkata to Bajkul (West Bengal)   
40                  Kolkata to Kirnahar (West Bengal)   
41                  Durgapur (West Bengal) to Bankura   
42                                  Siliguri to Malda   
43                                    Kolkata to Suri   
44                  Purulia to Durgapur (West Bengal)   

                                           Route link  
0   https://www.redbus.in/bus-tickets/burdwan-to-k...  
1   https://www.redbus.in/bus-tickets/kolkata-to-b...  
2   https://www.redbus.in/bus-tickets/durgapur-to-...  
3   https://www.redbus.in/bus-tickets/kolkata-to-h...  
4   https://www.redbus.in/bus-tickets/haldia-to-ko...  
5   https://www.redbus.in/bus-tickets/kolkata-to-d...  
6   https://www.redbus.in/bus-tickets/kolkata-to-a...  
7   https://www.redbus.in/bus-tickets/digha-to-kol...  
8   https://www.redbus.in/bus-tickets/kolkata-to-d...  
9   https://www.redbus.in/bus-tickets/kolkata-to-b...  
10  https://www.redbus.in/bus-tickets/asansol-to-k...  
11  https://www.redbus.in/bus-tickets/midnapore-to...  
12  https://www.redbus.in/bus-tickets/kolkata-to-a...  
13  https://www.redbus.in/bus-tickets/kolkata-to-s...  
14  https://www.redbus.in/bus-tickets/kolkata-to-n...  
15  https://www.redbus.in/bus-tickets/siliguri-to-...  
16  https://www.redbus.in/bus-tickets/kolkata-to-c...  
17  https://www.redbus.in/bus-tickets/digha-to-dur...  
18  https://www.redbus.in/bus-tickets/kolkata-to-m...  
19  https://www.redbus.in/bus-tickets/kolkata-to-n...  
20  https://www.redbus.in/bus-tickets/kolkata-to-m...  
21  https://www.redbus.in/bus-tickets/durgapur-to-...  
22  https://www.redbus.in/bus-tickets/kolkata-to-k...  
23  https://www.redbus.in/bus-tickets/jhargram-to-...  
24  https://www.redb

In [28]:
driver = webdriver.Chrome()

#Creating a list to store bus details

bus_details = []
#looping the each route links in the  dataframe :

for i in df['Route link']:

    driver.get(i) #

    full_url = driver.current_url
    driver.get(full_url + f'&onward=14-Aug-2024')

    time.sleep(2)  # Let the page load
    driver.maximize_window()
    
    # To get route name and route links
    try:
        route_name = driver.find_element(By.CLASS_NAME, 'D136_h1').text
        route_link = driver.current_url
    except Exception as e:
        print(f"Error retrieving route name or link: {e}")
        continue
    
    # Initialize WebDriverWait
    wait = WebDriverWait(driver, 20)  # Increased timeout

    # Wait for buttons to be visible and click them
    try:
        govt_buttons = wait.until(EC.visibility_of_all_elements_located((By.XPATH, './/div[@class="button"]')))
        for govt_button in govt_buttons[::-1]:
                driver.execute_script("window.scrollTo(0, 330);")
                govt_button.click()
                time.sleep(2)
                
    except Exception as e:
        print(f"Error waiting for buttons: {e}")
        continue
    time.sleep(3)

    # Scroll down to load more buses
    scroll_to_load(driver, 10)

    # Wait until all  bus items  present
    try:
        wait.until(EC.presence_of_all_elements_located((By.CLASS_NAME, 'bus-item')))  
        containers = driver.find_elements(By.CLASS_NAME, 'bus-item')
        for container in containers:
            try:
                bus_names = container.find_element(By.XPATH, './/div[@class="travels lh-24 f-bold d-color"]').text
                bus_type = container.find_element(By.XPATH, './/div[@class="bus-type f-12 m-top-16 l-color evBus"]').text
                departure_time = container.find_element(By.XPATH, './/div[@class="dp-time f-19 d-color f-bold"]').text
                duration = container.find_element(By.XPATH, './/div[@class="dur l-color lh-24"]').text
                reaching_time = container.find_element(By.XPATH, './/div[@class="bp-time f-19 d-color disp-Inline"]').text
                star_rating = container.find_element(By.XPATH,".//div[@class='column-six p-right-10 w-10 fl']").text
                price = container.find_element(By.XPATH, './/div[@class="fare d-block"]').text
                seat_availability = container.find_element(By.XPATH, './/div[contains(@class,"seat-left")]').text

                 
                bus_details.append({
                    "bus_name": bus_names,
                    "bus_type": bus_type,
                    "departure_time": departure_time,
                    "duration": duration,
                    "reaching_time": reaching_time,
                    "star_rating": star_rating,
                    "price": price,
                    "seat_availability": seat_availability,
                    "route_name": route_name,
                    "route_link": route_link
                })
            except Exception as e:
                print(f"Error extracting details: {e}")
    except Exception as e:
        print(f"Error waiting for bus items: {e}")

    

# Print the collected bus details
print(bus_details)



Error waiting for buttons: Message: 

['https://www.redbus.in/bus-tickets/kolkata-to-arambagh-west-bengal?fromCityId=74820&toCityId=201666&fromCityName=Kolkata&toCityName=Arambagh%20(West%20Bengal)&busType=Any&srcCountry=IND&destCountry=IND&onward=13-Aug-2024']


In [37]:
# Converting into DATAFRAME 

df_sbstc_details=pd.DataFrame(bus_details)
df_sbstc_details

bus_name  \
0       SBSTC-BURDWAN - KOLKATA - 05:45 (BWN DEPOT) - 2   
1     SBSTC-BURDWAN - KARUNAMOYEE - 05:50 (BWN DEPOT...   
2       SBSTC-BURDWAN - KOLKATA - 06:15 (BWN DEPOT) - 4   
3     SBSTC-BURDWAN - KARUNAMOYEE - 06:25 (BWN DEPOT...   
4     SBSTC-BURDWAN - KARUNAMOYEE - 07:10 (BWN DEPOT...   
...                                                 ...   
1843  SBSTC-BAGMUNDI - KOLKATA - 05:00 (BEL DEPOT) -...   
1844  SBSTC-PURULIA - KOLKATA - 07:15 - (VIA ASN) (H...   
1845  SBSTC-PURULIA - BERHAMPUR - 07:30 (PRL DEPOT) ...   
1846  SBSTC-PURULIA - KOLKATA - VIA - ASN - 09:15 (P...   
1847  WBTC (CTC) KOLKATA - ASANSOL - PURULIA (AC VOL...   

                   bus_type departure_time duration reaching_time star_rating  \
0       Non AC Seater (2+3)          05:45  02h 00m         07:45     4.5\n74   
1       Non AC Seater (2+3)          05:50  02h 30m         08:20    4.3\n145   
2       Non AC Seater (2+3)          06:15  02h 00m         08:15    3.9\n107   
3       Non AC Seater (2+3)          06:25  02h 30m         08:55    4.3\n115   
4       Non AC Seater (2+3)          07:10  02h 30m         09:40    3.9\n128   
...                     ...            ...      ...           ...         ...   
1843    Non AC Seater (2+3)          06:50  04h 00m         10:50         3.6   
1844    Non AC Seater (2+3)          07:15  03h 50m         11:05      4.0\n9   
1845    Non AC Seater (2+3)          07:30  03h 50m         11:20     3.4\n10   
1846    Non AC Seater (2+3)          09:15  04h 15m         13:30     4.0\n15   
1847  Volvo AC Seater (2+2)          05:45  03h 10m         08:55     3.9\n86   

        price   seat_availability                             route_name  \
0      INR 95  51 Seats available                 Burdwan to Kolkata Bus   
1     INR 100  20 Seats available                 Burdwan to Kolkata Bus   
2      INR 95  45 Seats available                 Burdwan to Kolkata Bus   
3     INR 100  18 Seats available                 Burdwan to Kolkata Bus   
4     INR 100  25 Seats available                 Burdwan to Kolkata Bus   
...       ...                 ...                                    ...   
1843  INR 117  52 Seats available  Purulia to Durgapur (West Bengal) Bus   
1844  INR 112  52 Seats available  Purulia to Durgapur (West Bengal) Bus   
1845  INR 112  52 Seats available  Purulia to Durgapur (West Bengal) Bus   
1846  INR 112  52 Seats available  Purulia to Durgapur (West Bengal) Bus   
1847  INR 240  36 Seats available  Purulia to Durgapur (West Bengal) Bus   

                                             route_link  
0     https://www.redbus.in/bus-tickets/burdwan-to-k...  
1     https://www.redbus.in/bus-tickets/burdwan-to-k...  
2     https://www.redbus.in/bus-tickets/burdwan-to-k...  
3     https://www.redbus.in/bus-tickets/burdwan-to-k...  
4     https://www.redbus.in/bus-tickets/burdwan-to-k...  
...                                                 ...  
1843  https://www.redbus.in/bus-tickets/purulia-to-d...  
1844  https://www.redbus.in/bus-tickets/purulia-to-d...  
1845  https://www.redbus.in/bus-tickets/purulia-to-d...  
1846  https://www.redbus.in/bus-tickets/purulia-to-d...  
1847  https://www.redbus.in/bus-tickets/purulia-to-d...  

[1848 rows x 10 columns]

In [38]:
#change dataframe to csv

df_sbstc_details.to_csv('sbstc_buses.csv', index=False)

HRTC bus details


In [39]:
#read csv file
df=pd.read_csv("hrtc_routes.csv")
df

Route name  \
0                                Delhi to Shimla   
1                                Shimla to Delhi   
2                           Manali to Chandigarh   
3                           Chandigarh to Manali   
4                                Delhi to Manali   
5      Hamirpur (Himachal Pradesh) to Chandigarh   
6           Delhi to Hamirpur (Himachal Pradesh)   
7                            Delhi to Chandigarh   
8                                Manali to Delhi   
9           Hamirpur (Himachal Pradesh) to Delhi   
10     Chandigarh to Hamirpur (Himachal Pradesh)   
11                              Shimla to Manali   
12       Delhi to Dharamshala (Himachal Pradesh)   
13                          Shimla to Chandigarh   
14  Chandigarh to Dharamshala (Himachal Pradesh)   
15             Delhi to Baddi (Himachal Pradesh)   
16  Dharamshala (Himachal Pradesh) to Chandigarh   
17       Chamba (Himachal Pradesh) to Chandigarh   
18                            Delhi to Dalhousie   
19            Delhi to Chamba (Himachal Pradesh)   
20                            Dalhousie to Delhi   
21                                Solan to Delhi   
22                             Delhi to Palampur   
23       Dharamshala (Himachal Pradesh) to Delhi   
24                                Delhi to Solan   
25  Chandigarh to Reckong Peo (Himachal Pradesh)   
26                              Manali to Shimla   
27                             Palampur to Delhi   
28                           Chandigarh to Kullu   
29                          Kangra to Chandigarh   
30                           Kullu to Chandigarh   
31                               Delhi to Kangra   
32            Chamba (Himachal Pradesh) to Delhi   
33                        Palampur to Chandigarh   
34                          Chandigarh to Shimla   
35                          Chandigarh to Kangra   
36                             Delhi to Nalagarh   
37             Baddi (Himachal Pradesh) to Delhi   
38                               Kangra to Delhi   
39                            Ghumarwin to Delhi   
40                            Delhi to Sarkaghat   

                                           Route link  
0   https://www.redbus.in/bus-tickets/delhi-to-shimla  
1   https://www.redbus.in/bus-tickets/shimla-to-delhi  
2   https://www.redbus.in/bus-tickets/manali-to-ch...  
3   https://www.redbus.in/bus-tickets/chandigarh-t...  
4   https://www.redbus.in/bus-tickets/delhi-to-manali  
5   https://www.redbus.in/bus-tickets/hamirpur-him...  
6   https://www.redbus.in/bus-tickets/delhi-to-ham...  
7   https://www.redbus.in/bus-tickets/delhi-to-cha...  
8   https://www.redbus.in/bus-tickets/manali-to-delhi  
9   https://www.redbus.in/bus-tickets/hamirpur-him...  
10  https://www.redbus.in/bus-tickets/chandigarh-t...  
11  https://www.redbus.in/bus-tickets/shimla-to-ma...  
12  https://www.redbus.in/bus-tickets/delhi-to-dha...  
13  https://www.redbus.in/bus-tickets/shimla-to-ch...  
14  https://www.redbus.in/bus-tickets/chandigarh-t...  
15  https://www.redbus.in/bus-tickets/delhi-to-bad...  
16  https://www.redbus.in/bus-tickets/dharamshala-...  
17  https://www.redbus.in/bus-tickets/chamba-himac...  
18  https://www.redbus.in/bus-tickets/delhi-to-dal...  
19  https://www.redbus.in/bus-tickets/delhi-to-cha...  
20  https://www.redbus.in/bus-tickets/dalhousie-to...  
21   https://www.redbus.in/bus-tickets/solan-to-delhi  
22  https://www.redbus.in/bus-tickets/delhi-to-pal...  
23  https://www.redbus.in/bus-tickets/dharamshala-...  
24   https://www.redbus.in/bus-tickets/delhi-to-solan  
25  https://www.redbus.in/bus-tickets/chandigarh-t...  
26  https://www.redbus.in/bus-tickets/manali-to-sh...  
27  https://www.redbus.in/bus-tickets/palampur-to-...  
28  https://www.redbus.in/bus-tickets/chandigarh-t...  
29  https://www.redbus.in/bus-tickets/kangra-to-ch...  
30  https://www.redbus.in/bus-tickets/kullu-to-cha...  
31  https://www.redbus.in/bus-tickets/delhi-to-kangra  
32  h

In [40]:
driver = webdriver.Chrome()

#Creating a list to store bus details

bus_details = []

#looping the each route links in the  dataframe :

for i in df["Route link"]:

    driver.get(i) #

    full_url = driver.current_url
    driver.get(full_url + f'&onward=14-Aug-2024')

    time.sleep(2)  # Let the page load
    driver.maximize_window()
    
    # To get route name and route links
    try:
        route_name = driver.find_element(By.CLASS_NAME, 'D136_h1').text
        route_link = driver.current_url
    except Exception as e:
        print(f"Error retrieving route name or link: {e}")
        continue
    
    # Initialize WebDriverWait
    wait = WebDriverWait(driver, 20)  # Increased timeout

    # Wait for buttons to be visible and click them
    try:
        govt_buttons = wait.until(EC.visibility_of_all_elements_located((By.XPATH, './/div[@class="button"]')))
        for govt_button in govt_buttons[::-1]:
                driver.execute_script("window.scrollTo(0, 330);")
                govt_button.click()
                time.sleep(2)
                
    except Exception as e:
        print(f"Error waiting for buttons: {e}")
        continue

    # Scroll down to load more buses
    scroll_to_load(driver, 10)

    # Wait until all  bus items  present
    try:
        wait.until(EC.presence_of_all_elements_located((By.CLASS_NAME, 'bus-item')))
        containers = driver.find_elements(By.CLASS_NAME, 'bus-item')
        for container in containers:
            try:
                bus_names = container.find_element(By.XPATH, './/div[@class="travels lh-24 f-bold d-color"]').text
                bus_type = container.find_element(By.XPATH, './/div[@class="bus-type f-12 m-top-16 l-color evBus"]').text
                departure_time = container.find_element(By.XPATH, './/div[@class="dp-time f-19 d-color f-bold"]').text
                duration = container.find_element(By.XPATH, './/div[@class="dur l-color lh-24"]').text
                reaching_time = container.find_element(By.XPATH, './/div[@class="bp-time f-19 d-color disp-Inline"]').text
                star_rating = container.find_element(By.XPATH,".//div[@class='column-six p-right-10 w-10 fl']").text
                price = container.find_element(By.XPATH, './/div[@class="fare d-block"]').text
                seat_availability = container.find_element(By.XPATH, './/div[contains(@class,"seat-left")]').text

                 
                bus_details.append({
                    "bus_name": bus_names,
                    "bus_type": bus_type,
                    "departure_time": departure_time,
                    "duration": duration,
                    "reaching_time": reaching_time,
                    "star_rating": star_rating,
                    "price": price,
                    "seat_availability": seat_availability,
                    "route_name": route_name,
                    "route_link": route_link
                })
            except Exception as e:
                print(f"Error extracting details: {e}")
    except Exception as e:
        print(f"Error waiting for bus items: {e}")

    

# Print the collected bus details
print(bus_details)



Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

[{'bus_name': 'HRTC - 69', 'bus_type': 'Himsuta AC Seater Volvo/Scania 2+2', 'departure_time': '00:40', 'duration': '08h 50m', 'reaching_time': '09:30', 'star_rating': '4.6\n48', 'price': 'INR 892', 'seat_availability': '29 Seats available', 'route_name': 'Delhi to Shimla Bus', 'route_link': 'https://www.redbus.in/bus-tickets/delhi-to-shimla?fromCityId=733&toCityId=1285&fromCityName=Delhi&toCityName=Shimla&busType=Any&onward=12-Aug-2024&onward=14-Aug-2024'}, {'bus_name': 'HRTC - 2100720', 'bus_type': 'Ordinary 3+2 Non AC Seater', 'departure_time': '05:00', 'duration': '09h 50m', 'reaching_time': '14:50', 'star_ra

In [41]:
# Converting into DATAFRAME 

df_hrtc_details=pd.DataFrame(bus_details)
df_hrtc_details

bus_name                                 bus_type  \
0                          HRTC - 69       Himsuta AC Seater Volvo/Scania 2+2   
1                     HRTC - 2100720               Ordinary 3+2 Non AC Seater   
2                           HRTC - 6       Himsuta AC Seater Volvo/Scania 2+2   
3                         HRTC - 592                      A/C Executive (2+3)   
4                         HRTC - 129               Ordinary 3+2 Non AC Seater   
...                              ...                                      ...   
1842                Northern Travels             Volvo A/C Semi Sleeper (2+2)   
1843               City Land Travels             Volvo A/C Semi Sleeper (2+2)   
1844                         FlixBus                         A/C Seater (2+2)   
1845                    A N Holidays       Bharat Benz A/C Semi Sleeper (2+2)   
1846  Kartar Travels Private Limited  Scania Multi-Axle AC Semi Sleeper (2+2)   

     departure_time duration reaching_time star_rating    price  \
0             00:40  08h 50m         09:30     4.6\n48  INR 892   
1             05:00  09h 50m         14:50         4.2  INR 507   
2             06:45  09h 25m         16:10     4.6\n61  INR 892   
3             08:05  10h 05m         18:10     2.3\n13  INR 622   
4             08:50  09h 50m         18:40      2.5\n5  INR 507   
...             ...      ...           ...         ...      ...   
1842          19:45  09h 30m         05:15     2.5\n40      570   
1843          19:40  09h 30m         05:10     3.9\n22      630   
1844          18:40  10h 40m         05:20     4.2\n14  INR 678   
1845          20:10  10h 05m         06:15     3.6\n14      574   
1846          21:45  09h 30m         07:15         2.7     1899   

       seat_availability           route_name  \
0     29 Seats available  Delhi to Shimla Bus   
1     37 Seats available  Delhi to Shimla Bus   
2     29 Seats available  Delhi to Shimla Bus   
3     42 Seats available  Delhi to Shimla Bus   
4     37 Seats available  Delhi to Shimla Bus   
...                  ...                  ...   
1842  38 Seats available  Kangra to Delhi Bus   
1843  34 Seats available  Kangra to Delhi Bus   
1844  39 Seats available  Kangra to Delhi Bus   
1845  32 Seats available  Kangra to Delhi Bus   
1846  49 Seats available  Kangra to Delhi Bus   

                                             route_link  
0     https://www.redbus.in/bus-tickets/delhi-to-shi...  
1     https://www.redbus.in/bus-tickets/delhi-to-shi...  
2     https://www.redbus.in/bus-tickets/delhi-to-shi...  
3     https://www.redbus.in/bus-tickets/delhi-to-shi...  
4     https://www.redbus.in/bus-tickets/delhi-to-shi...  
...                                                 ...  
1842  https://www.redbus.in/bus-tickets/kangra-to-de...  
1843  https://www.redbus.in/bus-tickets/kangra-to-de...  
1844  https://www.redbus.in/bus-tickets/kangra-to-de...  
1845  https://www.redbus.in/bus-tickets/kangra-to-de...  
1846  https://www.redbus.in/bus-tickets/kangra-to-de...  

[1847 rows x 10 columns]

In [42]:
#change dataframe to csv

df_hrtc_details.to_csv('hrtc_buses.csv', index=False)

ASTC Bus details

In [4]:
#read csv file
df=pd.read_csv("astc_routes.csv")
df

Route name  \
0               Tezpur to Guwahati   
1               Guwahati to Tezpur   
2       Nagaon (Assam) to Guwahati   
3       Guwahati to Nagaon (Assam)   
4             Goalpara to Guwahati   
5        Jorhat to North Lakhimpur   
6               Dhubri to Guwahati   
7               Guwahati to Dhubri   
8      North Lakhimpur to Sibsagar   
9        North Lakhimpur to Jorhat   
10          Dhekiajuli to Guwahati   
11             Jorhat to Dibrugarh   
12               Jorhat to Dhemaji   
13     Sibsagar to North Lakhimpur   
14               Dhemaji to Jorhat   
15             Tezpur to Dibrugarh   
16             Haflong to Guwahati   
17    North Lakhimpur to Dibrugarh   
18              Jorhat to Tinsukia   
19             Dibrugarh to Tezpur   
20   Guwahati to Biswanath Charali   
21             Guwahati to Haflong   
22    Dibrugarh to North Lakhimpur   
23       Nagaon (Assam) to Haflong   
24                 Tezpur to Moran   
25             Dibrugarh to Jorhat   
26             Guwahati to Silchar   
27           Bihpuria to Dibrugarh   
28       Haflong to Nagaon (Assam)   
29       North Lakhimpur to Tezpur   
30   Biswanath Charali to Guwahati   
31  Biswanath Charali to Dibrugarh   
32              Tinsukia to Jorhat   
33                 Moran to Tezpur   
34              Jorhat to Gogamukh   
35  Dibrugarh to Biswanath Charali   
36              Gohpur to Guwahati   
37              Tinsukia to Tezpur   
38     North Lakhimpur to Golaghat   
39     Golaghat to North Lakhimpur   
40             Silchar to Guwahati   
41           Bokakhat to Dibrugarh   
42        North Lakhimpur to Moran   
43       Tezpur to North Lakhimpur   
44              Tezpur to Tinsukia   
45           Dibrugarh to Bihpuria   
46           Dibrugarh to Bokakhat   

                                           Route link  
0   https://www.redbus.in/bus-tickets/tezpur-to-gu...  
1   https://www.redbus.in/bus-tickets/guwahati-to-...  
2   https://www.redbus.in/bus-tickets/nagaon-to-gu...  
3   https://www.redbus.in/bus-tickets/guwahati-to-...  
4   https://www.redbus.in/bus-tickets/goalpara-to-...  
5   https://www.redbus.in/bus-tickets/jorhat-to-no...  
6   https://www.redbus.in/bus-tickets/dhubri-to-gu...  
7   https://www.redbus.in/bus-tickets/guwahati-to-...  
8   https://www.redbus.in/bus-tickets/north-lakhim...  
9   https://www.redbus.in/bus-tickets/north-lakhim...  
10  https://www.redbus.in/bus-tickets/dhekiajuli-t...  
11  https://www.redbus.in/bus-tickets/jorhat-to-di...  
12  https://www.redbus.in/bus-tickets/jorhat-to-dh...  
13  https://www.redbus.in/bus-tickets/sibsagar-to-...  
14  https://www.redbus.in/bus-tickets/dhemaji-to-j...  
15  https://www.redbus.in/bus-tickets/tezpur-to-di...  
16  https://www.redbus.in/bus-tickets/haflong-to-g...  
17  https://www.redbus.in/bus-tickets/north-lakhim...  
18  https://www.redbus.in/bus-tickets/jorhat-to-ti...  
19  https://www.redbus.in/bus-tickets/dibrugarh-to...  
20  https://www.redbus.in/bus-tickets/guwahati-to-...  
21  https://www.redbus.in/bus-tickets/guwahati-to-...  
22  https://www.redbus.in/bus-tickets/dibrugarh-to...  
23  https://www.redbus.in/bus-tickets/nagaon-to-ha...  
24  https://www.redbus.in/bus-tickets/tezpur-to-moran  
25  https://www.redbus.in/bus-tickets/dibrugarh-to...  
26  https://www.redbus.in/bus-tickets/guwahati-to-...  
27  https://www.redbus.in/bus-tickets/bihpuria-to-...  
28  https://www.redbus.in/bus-tickets/haflong-to-n...  
29  https://www.redbus.in/bus-tickets/north-lakhim...  
30  https://www.redbus.in/bus-tickets/biswanath-ch...  
31  https://www.redbus.in/bus-tickets/biswanath-ch...  
32  https://www.redbus.in/bus-tickets/tinsukia-to-...  
33  https://www.redbus.in/bus-tickets/moran-to-tezpur  
34  https://www.redbus.in/bus-tickets/jorhat-to-go...  
35  https://www.redbus.in/bus-tickets/dibrugarh-to...  
36  https://www.redbus.in/bus-tickets/gohpur-to-gu...  
37  https://www.redbus.in/bus-tickets/tinsukia-to-...  
38  https://www

In [5]:
driver = webdriver.Chrome()

#Creating a list to store bus details

bus_details = []

#looping the each route links in the  dataframe :

for i in df["Route link"]:

    driver.get(i) #

    full_url = driver.current_url
    driver.get(full_url + f'&onward=14-Aug-2024')

    time.sleep(2)  # Let the page load
    driver.maximize_window()
    
    # To get route name and route links
    try:
        route_name = driver.find_element(By.CLASS_NAME, 'D136_h1').text
        route_link = driver.current_url
    except Exception as e:
        print(f"Error retrieving route name or link: {e}")
        continue
    
    # Initialize WebDriverWait
    wait = WebDriverWait(driver, 20)  # Increased timeout

    # Wait for buttons to be visible and click them
    try:
        govt_buttons = wait.until(EC.visibility_of_all_elements_located((By.XPATH, './/div[@class="button"]')))
        for govt_button in govt_buttons[::-1]:
                driver.execute_script("window.scrollTo(0, 330);")
                govt_button.click()
                time.sleep(2)
                
    except Exception as e:
        print(f"Error waiting for buttons: {e}")
        continue

    # Scroll down to load more buses
    scroll_to_load(driver, 10)

    # Wait until all  bus items  present
    try:
        wait.until(EC.presence_of_all_elements_located((By.CLASS_NAME, 'bus-item')))
        containers = driver.find_elements(By.CLASS_NAME, 'bus-item')
        for container in containers:
            try:
                bus_names = container.find_element(By.XPATH, './/div[@class="travels lh-24 f-bold d-color"]').text
                bus_type = container.find_element(By.XPATH, './/div[@class="bus-type f-12 m-top-16 l-color evBus"]').text
                departure_time = container.find_element(By.XPATH, './/div[@class="dp-time f-19 d-color f-bold"]').text
                duration = container.find_element(By.XPATH, './/div[@class="dur l-color lh-24"]').text
                reaching_time = container.find_element(By.XPATH, './/div[@class="bp-time f-19 d-color disp-Inline"]').text
                star_rating = container.find_element(By.XPATH,".//div[@class='column-six p-right-10 w-10 fl']").text
                price = container.find_element(By.XPATH, './/div[@class="fare d-block"]').text
                seat_availability = container.find_element(By.XPATH, './/div[contains(@class,"seat-left")]').text

                 
                bus_details.append({
                    "bus_name": bus_names,
                    "bus_type": bus_type,
                    "departure_time": departure_time,
                    "duration": duration,
                    "reaching_time": reaching_time,
                    "star_rating": star_rating,
                    "price": price,
                    "seat_availability": seat_availability,
                    "route_name": route_name,
                    "route_link": route_link
                })
            except Exception as e:
                print(f"Error extracting details: {e}")
    except Exception as e:
        print(f"Error waiting for bus items: {e}")

    

# Print the collected bus details
print(bus_details)



Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waitin

In [6]:
# Converting into DATAFRAME 

df_astc_details=pd.DataFrame(bus_details)
df_astc_details

bus_name  \
0    Assam State Transport Corporation (ASTC) - 147480   
1    Assam State Transport Corporation (ASTC) - 174840   
2    Assam State Transport Corporation (ASTC) - 135927   
3    Assam State Transport Corporation (ASTC) - 156590   
4    Assam State Transport Corporation (ASTC) - 161055   
..                                                 ...   
149                                    NETWORK TRAVELS   
150                               Purple Wings Coaches   
151                                    NETWORK TRAVELS   
152                                  Christina Travels   
153                                          Maa Laxmi   

                           bus_type departure_time duration reaching_time  \
0      Bharat Benz A/C Seater (2+2)          05:00  04h 00m         09:00   
1      Bharat Benz A/C Seater (2+2)          06:15  04h 15m         10:30   
2               Volvo AC Seater 2+2          07:10  04h 30m         11:40   
3      Bharat Benz A/C Seater (2+2)          14:00  04h 30m         18:30   
4               Volvo AC Seater 2+2          16:15  04h 15m         20:30   
..                              ...            ...      ...           ...   
149  Non A/C Seater / Sleeper (2+1)          17:00  06h 00m         23:00   
150      A/C Seater / Sleeper (2+1)          18:30  05h 45m         00:15   
151  NON A/C Seater Push Back (2+1)          19:00  05h 30m         00:30   
152            NON A/C Seater (2+2)          07:00  04h 15m         11:15   
153  NON A/C Seater Push Back (2+1)          16:00  05h 30m         21:30   

    star_rating    price   seat_availability              route_name  \
0      3.8\n317  INR 270  29 Seats available  Tezpur to Guwahati Bus   
1        4.8\n5  INR 298  31 Seats available  Tezpur to Guwahati Bus   
2      4.2\n340  INR 298  30 Seats available  Tezpur to Guwahati Bus   
3       4.3\n31  INR 298  30 Seats available  Tezpur to Guwahati Bus   
4       4.3\n31  INR 298   8 Seats available  Tezpur to Guwahati Bus   
..          ...      ...                 ...                     ...   
149         4.3      350  48 Seats available  Tinsukia to Jorhat Bus   
150      3.7\n5      567  43 Seats available  Tinsukia to Jorhat Bus   
151     4.6\n25      300  33 Seats available  Tinsukia to Jorhat Bus   
152         2.8      650  31 Seats available  Tinsukia to Jorhat Bus   
153      2.1\n5  INR 400  36 Seats available  Tinsukia to Jorhat Bus   

                                            route_link  
0    https://www.redbus.in/bus-tickets/tezpur-to-gu...  
1    https://www.redbus.in/bus-tickets/tezpur-to-gu...  
2    https://www.redbus.in/bus-tickets/tezpur-to-gu...  
3    https://www.redbus.in/bus-tickets/tezpur-to-gu...  
4    https://www.redbus.in/bus-tickets/tezpur-to-gu...  
..                                                 ...  
149  https://www.redbus.in/bus-tickets/tinsukia-to-...  
150  https://www.redbus.in/bus-tickets/tinsukia-to-...  
151  https://www.redbus.in/bus-tickets/tinsukia-to-...  
152  https://www.redbus.in/bus-tickets/tinsukia-to-...  
153  https://www.redbus.in/bus-tickets/tinsukia-to-...  

[154 rows x 10 columns]

In [7]:
#change dataframe to csv

df_astc_details.to_csv('astc_buses.csv', index=False)

CTU BUS DETAILS

In [10]:
#read csv file
df=pd.read_csv("ctu_routes.csv")
df

Route name  \
0                            Chandigarh to Delhi   
1                            Delhi to Chandigarh   
2                     Yamuna Nagar to Chandigarh   
3                           Chandigarh to Shimla   
4                        Chandigarh to Vrindavan   
5                     Chandigarh to Yamuna Nagar   
6      Chandigarh to Sujanpur (himachal pradesh)   
7                         Ludhiana to Chandigarh   
8      Hamirpur (Himachal Pradesh) to Chandigarh   
9                        Vrindavan to Chandigarh   
10     Chandigarh to Hamirpur (Himachal Pradesh)   
11     Sujanpur (himachal pradesh) to Chandigarh   
12                          Shimla to Chandigarh   
13                        Chandigarh to Ludhiana   
14  Chandigarh to Dharamshala (Himachal Pradesh)   
15                        Chandigarh to Dehradun   
16                        Chandigarh to Baijnath   
17                       Pathankot to Chandigarh   
18                        Chandigarh to Haridwar   
19                       Chandigarh to Pathankot   
20                         Talwara to Chandigarh   
21                        Dehradun to Chandigarh   
22                        Amritsar to Chandigarh   
23                       Chandigarh to Rishikesh   
24                         Chandigarh to Talwara   
25              Chandigarh to Dinanagar (punjab)   
26              Dinanagar (punjab) to Chandigarh   
27                       Rishikesh to Chandigarh   
28                        Chandigarh to Amritsar   
29                            Chandigarh to Agra   
30  Dharamshala (Himachal Pradesh) to Chandigarh   
31       Chandigarh to Katra (jammu and kashmir)   
32                 Hisar (Haryana) to Chandigarh   
33                          Rohtak to Chandigarh   
34          Chandigarh to Una (Himachal Pradesh)   
35                 Chandigarh to Jammu (j and k)   
36                          Chandigarh to Rohtak   
37                          Chandigarh to Manali   
38                        Chandigarh to Haldwani   
39                       Jawala Ji to Chandigarh   
40                            Agra to Chandigarh   
41                 Jammu (j and k) to Chandigarh   
42                 Chandigarh to Hisar (Haryana)   
43                       Chandigarh to Kathgodam   
44                        Haridwar to Chandigarh   
45       Katra (jammu and kashmir) to Chandigarh   
46                        Baijnath to Chandigarh   
47                         Narnaul to Chandigarh   
48                       Chandigarh to Jawala Ji   

                                           Route link  
0   https://www.redbus.in/bus-tickets/chandigarh-t...  
1   https://www.redbus.in/bus-tickets/delhi-to-cha...  
2   https://www.redbus.in/bus-tickets/yamuna-nagar...  
3   https://www.redbus.in/bus-tickets/chandigarh-t...  
4   https://www.redbus.in/bus-tickets/chandigarh-t...  
5   https://www.redbus.in/bus-tickets/chandigarh-t...  
6   https://www.redbus.in/bus-tickets/chandigarh-t...  
7   https://www.redbus.in/bus-tickets/ludhiana-to-...  
8   https://www.redbus.in/bus-tickets/hamirpur-him...  
9   https://www.redbus.in/bus-tickets/vrindavan-to...  
10  https://www.redbus.in/bus-tickets/chandigarh-t...  
11  https://www.redbus.in/bus-tickets/sujanpur-to-...  
12  https://www.redbus.in/bus-tickets/shimla-to-ch...  
13  https://www.redbus.in/bus-tickets/chandigarh-t...  
14  https://www.redbus.in/bus-tickets/chandigarh-t...  
15  https://www.redbus.in/bus-tickets/chandigarh-t...  
16  https://www.redbus.in/bus-tickets/chandigarh-t...  
17  https://www.redbus.in/bus-tickets/pathankot-to...  
18  https://www.redbus.in/bus-tickets/chandigarh-t...  
19  https://www.redbus.in/bus-tickets/chandigarh-t...  
20  https://www.redbus.in/bus-tickets/talwara-to-c...  
21  https://www.redbus.in/bus-tickets/dehradun-to-...  
22  https://www.redbus.in/bus-tickets/amritsar-to-...  
23  https://www.redbus.in/bus-tickets/chandigarh-t...  
24  https://www.redbus.in/bus-tickets

In [12]:
driver = webdriver.Chrome()

#Creating a list to store bus details

bus_details = []

#looping the each route links in the  dataframe :

for i in df["Route link"]:

    driver.get(i) #

    full_url = driver.current_url
    driver.get(full_url + f'&onward=14-Aug-2024')

    time.sleep(2)  # Let the page load
    driver.maximize_window()
    
    # To get route name and route links
    try:
        route_name = driver.find_element(By.CLASS_NAME, 'D136_h1').text
        route_link = driver.current_url
    except Exception as e:
        print(f"Error retrieving route name or link: {e}")
        continue
    
    # Initialize WebDriverWait
    wait = WebDriverWait(driver, 20)  # Increased timeout

    # Wait for buttons to be visible and click them
    try:
        govt_buttons = wait.until(EC.visibility_of_all_elements_located((By.XPATH, './/div[@class="button"]')))
        for govt_button in govt_buttons[::-1]:
                driver.execute_script("window.scrollTo(0, 330);")
                govt_button.click()
                time.sleep(2)
                
    except Exception as e:
        print(f"Error waiting for buttons: {e}")
        continue

    # Scroll down to load more buses
    scroll_to_load(driver, 10)

    # Wait until all  bus items  present
    try:
        wait.until(EC.presence_of_all_elements_located((By.CLASS_NAME, 'bus-item')))
        containers = driver.find_elements(By.CLASS_NAME, 'bus-item')
        for container in containers:
            try:
                bus_names = container.find_element(By.XPATH, './/div[@class="travels lh-24 f-bold d-color"]').text
                bus_type = container.find_element(By.XPATH, './/div[@class="bus-type f-12 m-top-16 l-color evBus"]').text
                departure_time = container.find_element(By.XPATH, './/div[@class="dp-time f-19 d-color f-bold"]').text
                duration = container.find_element(By.XPATH, './/div[@class="dur l-color lh-24"]').text
                reaching_time = container.find_element(By.XPATH, './/div[@class="bp-time f-19 d-color disp-Inline"]').text
                star_rating = container.find_element(By.XPATH,".//div[@class='column-six p-right-10 w-10 fl']").text
                price = container.find_element(By.XPATH, './/div[@class="fare d-block"]').text
                seat_availability = container.find_element(By.XPATH, './/div[contains(@class,"seat-left")]').text

                 
                bus_details.append({
                    "bus_name": bus_names,
                    "bus_type": bus_type,
                    "departure_time": departure_time,
                    "duration": duration,
                    "reaching_time": reaching_time,
                    "star_rating": star_rating,
                    "price": price,
                    "seat_availability": seat_availability,
                    "route_name": route_name,
                    "route_link": route_link
                })
            except Exception as e:
                print(f"Error extracting details: {e}")
    except Exception as e:
        print(f"Error waiting for bus items: {e}")

    

# Print the collected bus details
print(bus_details)



Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

[{'bus_name': 'Chandigarh Transport Undertaking (CTU) - 165681', 'bus_type': 'HVAC Seater (2+3)', 'departure_time': '07:00', 'duration': '05h 35m', 'reaching_time': '12:35', 'star_rating': '4.0\n49', 'price': 'INR 404.76', 'seat_availability': '45 Seats available', 'route_name': 'Chandigarh to Delhi Bus', 'route_link': 'https://www.redbus.in/bus-ticket

In [13]:
# Converting into DATAFRAME 

df_ctu_details=pd.DataFrame(bus_details)
df_ctu_details

bus_name  \
0       Chandigarh Transport Undertaking (CTU) - 165681   
1       Chandigarh Transport Undertaking (CTU) - 165684   
2       Chandigarh Transport Undertaking (CTU) - 165687   
3       Chandigarh Transport Undertaking (CTU) - 165676   
4       Chandigarh Transport Undertaking (CTU) - 165689   
...                                                 ...   
1560  Asian's Shina Tour & Travels (Swoyambhu Manjus...   
1561                                   PAL Travel Lines   
1562                                   Northern Travels   
1563                                   PAL Travel Lines   
1564  Asian's Shina Tour & Travels (Swoyambhu Manjus...   

                                bus_type departure_time duration  \
0                      HVAC Seater (2+3)          07:00  05h 35m   
1                      HVAC Seater (2+3)          07:55  05h 35m   
2                      HVAC Seater (2+3)          08:25  05h 35m   
3                      HVAC Seater (2+3)          09:25  05h 35m   
4                      HVAC Seater (2+3)          10:30  05h 35m   
...                                  ...            ...      ...   
1560              A/C Semi Sleeper (2+2)          00:29  04h 31m   
1561        Volvo A/C Semi Sleeper (2+2)          00:45  03h 55m   
1562        Volvo A/C Semi Sleeper (2+2)          01:20  04h 55m   
1563  Bharat Benz A/C Semi Sleeper (2+2)          02:04  04h 01m   
1564          NON A/C Semi Sleeper (2+2)          23:55  05h 05m   

     reaching_time star_rating       price   seat_availability  \
0            12:35     4.0\n49  INR 404.76  45 Seats available   
1            13:30     4.0\n16  INR 404.76  47 Seats available   
2            14:00     3.8\n26  INR 404.76  47 Seats available   
3            15:00     4.1\n26  INR 404.76  47 Seats available   
4            16:05     3.6\n33  INR 404.76  47 Seats available   
...            ...         ...         ...                 ...   
1560         05:00         2.4     INR 999    1 Seat available   
1561         04:40         2.9        1439  31 Seats available   
1562         06:15         2.7         636  23 Seats available   
1563         06:05         2.9        1619  16 Seats available   
1564         05:00         2.4    INR 1499  28 Seats available   

                       route_name  \
0         Chandigarh to Delhi Bus   
1         Chandigarh to Delhi Bus   
2         Chandigarh to Delhi Bus   
3         Chandigarh to Delhi Bus   
4         Chandigarh to Delhi Bus   
...                           ...   
1560  Chandigarh to Jawala Ji Bus   
1561  Chandigarh to Jawala Ji Bus   
1562  Chandigarh to Jawala Ji Bus   
1563  Chandigarh to Jawala Ji Bus   
1564  Chandigarh to Jawala Ji Bus   

                                             route_link  
0     https://www.redbus.in/bus-tickets/chandigarh-t...  
1     https://www.redbus.in/bus-tickets/chandigarh-t...  
2     https://www.redbus.in/bus-tickets/chandigarh-t...  
3     https://www.redbus.in/bus-tickets/chandigarh-t...  
4     https://www.redbus.in/bus-tickets/chandigarh-t...  
...                                                 ...  
1560  https://www.redbus.in/bus-tickets/chandigarh-t...  
1561  https://www.redbus.in/bus-tickets/chandigarh-t...  
1562  https://www.redbus.in/bus-tickets/chandigarh-t...  
1563  https://www.redbus.in/bus-tickets/chandigarh-t...  
1564  https://www.redbus.in/bus-tickets/chandigarh-t...  

[1565 rows x 10 columns]

In [14]:
#change dataframe to csv

df_ctu_details.to_csv('ctu_buses.csv', index=False)

PEPSU Bus Details

In [15]:
#read csv file
df=pd.read_csv("pepsu_routes.csv")
df

Route name  \
0             Patiala to Delhi   
1             Delhi to Patiala   
2            Ludhiana to Delhi   
3            Delhi to Ludhiana   
4            Phagwara to Delhi   
5           Jalandhar to Delhi   
6           Delhi to Jalandhar   
7     Patiala to Delhi Airport   
8   Jalandhar to Delhi Airport   
9    Ludhiana to Delhi Airport   
10   Phagwara to Delhi Airport   
11   Delhi Airport to Ludhiana   
12           Delhi to Phagwara   
13           Delhi to Amritsar   
14           Amritsar to Delhi   
15    Delhi Airport to Patiala   
16   Amritsar to Delhi Airport   
17         Kapurthala to Delhi   
18  Delhi Airport to Jalandhar   
19      Chandigarh to Bathinda   
20      Chandigarh to Faridkot   
21       Chandigarh to Patiala   

                                           Route link  
0   https://www.redbus.in/bus-tickets/patiala-to-d...  
1   https://www.redbus.in/bus-tickets/delhi-to-pat...  
2   https://www.redbus.in/bus-tickets/ludhiana-to-...  
3   https://www.redbus.in/bus-tickets/delhi-to-lud...  
4   https://www.redbus.in/bus-tickets/phagwara-to-...  
5   https://www.redbus.in/bus-tickets/jalandhar-to...  
6   https://www.redbus.in/bus-tickets/delhi-to-jal...  
7   https://www.redbus.in/bus-tickets/patiala-to-d...  
8   https://www.redbus.in/bus-tickets/jalandhar-to...  
9   https://www.redbus.in/bus-tickets/ludhiana-to-...  
10  https://www.redbus.in/bus-tickets/phagwara-to-...  
11  https://www.redbus.in/bus-tickets/delhi-airpor...  
12  https://www.redbus.in/bus-tickets/delhi-to-pha...  
13  https://www.redbus.in/bus-tickets/delhi-to-amr...  
14  https://www.redbus.in/bus-tickets/amritsar-to-...  
15  https://www.redbus.in/bus-tickets/delhi-airpor...  
16  https://www.redbus.in/bus-tickets/amritsar-to-...  
17  https://www.redbus.in/bus-tickets/kapurthala-t...  
18  https://www.redbus.in/bus-tickets/delhi-airpor...  
19  https://www.redbus.in/bus-tickets/chandigarh-t...  
20  https://www.redbus.in/bus-tickets/chandigarh-t...  
21  https://www.redbus.in/bus-tickets/chandigarh-t...

In [19]:
driver = webdriver.Chrome()

#Creating a list to store bus details

bus_details = []

#looping the each route links in the  dataframe :

for i in df["Route link"]:

    driver.get(i) #

    full_url = driver.current_url
    driver.get(full_url + f'&onward=14-Aug-2024')

    time.sleep(2)  # Let the page load
    driver.maximize_window()
    
    # To get route name and route links
    try:
        route_name = driver.find_element(By.CLASS_NAME, 'D136_h1').text
        route_link = driver.current_url
    except Exception as e:
        print(f"Error retrieving route name or link: {e}")
        continue
    
    # Initialize WebDriverWait
    wait = WebDriverWait(driver, 20)  # Increased timeout
    
    
    # Wait for buttons to be visible and click them
    try:
        govt_buttons = wait.until(EC.visibility_of_all_elements_located((By.XPATH, './/div[@class="button"]')))
        for govt_button in govt_buttons[::-1]:
                driver.execute_script("window.scrollTo(0, 330);")
                govt_button.click()
                time.sleep(2)
                
    except Exception as e:
        print(f"Error waiting for buttons: {e}")
        continue
    
    # Scroll down to load more buses
    scroll_to_load(driver, 10)

    # Wait until all  bus items  present
    try:
        wait.until(EC.presence_of_all_elements_located((By.CLASS_NAME, 'bus-item')))
        containers = driver.find_elements(By.CLASS_NAME, 'bus-item')
        for container in containers:
            try:
                bus_names = container.find_element(By.XPATH, './/div[@class="travels lh-24 f-bold d-color"]').text
                bus_type = container.find_element(By.XPATH, './/div[@class="bus-type f-12 m-top-16 l-color evBus"]').text
                departure_time = container.find_element(By.XPATH, './/div[@class="dp-time f-19 d-color f-bold"]').text
                duration = container.find_element(By.XPATH, './/div[@class="dur l-color lh-24"]').text
                reaching_time = container.find_element(By.XPATH, './/div[@class="bp-time f-19 d-color disp-Inline"]').text
                star_rating = container.find_element(By.XPATH,".//div[@class='column-six p-right-10 w-10 fl']").text
                price = container.find_element(By.XPATH, './/div[@class="fare d-block"]').text
                seat_availability = container.find_element(By.XPATH, './/div[contains(@class,"seat-left")]').text

                 
                bus_details.append({
                    "bus_name": bus_names,
                    "bus_type": bus_type,
                    "departure_time": departure_time,
                    "duration": duration,
                    "reaching_time": reaching_time,
                    "star_rating": star_rating,
                    "price": price,
                    "seat_availability": seat_availability,
                    "route_name": route_name,
                    "route_link": route_link
                })
            except Exception as e:
                print(f"Error extracting details: {e}")
    except Exception as e:
        print(f"Error waiting for bus items: {e}")

    

# Print the collected bus details
print(bus_details)



Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

[{'bus_name': 'PEPSU (Punjab) - 67134', 'bus_type': 'Volvo AC Seater (2+2)', 'departure_time': '06:40', 'duration': '06h 35m', 'reaching_time': '13:15', 'star_rating': '4.0\n56', 'price': 'INR 845', 'seat_availability': '38 Seats available', 'route_name': 'Ludhiana to Delhi Bus', 'route_link': 'https://www.redbus.in/bus-tickets/ludhiana-to-delhi?fromCityId=736&toCityId=733&fromCityName=Ludhiana&toCityName=Delhi&busType=Any&onward=13-Aug-2024&onward=14-Aug-2024'}, {'bus_name': 'PEPSU (Punjab) - 67161', 'bus_type': 'Volvo AC Seater (2+2)', 'departure_time': '10:15', 'duration': '07h 00m', 'reaching_time': '17:15', 'star_rating': '4.0\n19', 'price': 'INR 845', 'seat_availability': '33 Seats available', 'route_name': 'Ludhiana t

In [20]:
# Converting into DATAFRAME 

df_pepsu_details=pd.DataFrame(bus_details)
df_pepsu_details

bus_name                bus_type departure_time  \
0               PEPSU (Punjab) - 67134   Volvo AC Seater (2+2)          06:40   
1               PEPSU (Punjab) - 67161   Volvo AC Seater (2+2)          10:15   
2               PEPSU (Punjab) - 67162   Volvo AC Seater (2+2)          15:00   
3               PEPSU (Punjab) - 67096   Volvo AC Seater (2+2)          16:10   
4               PEPSU (Punjab) - 67135   Volvo AC Seater (2+2)          17:35   
..                                 ...                     ...            ...   
718  Indo Canadian Transport Pvt. Ltd.  A/C Semi Sleeper (2+2)          12:00   
719  Indo Canadian Transport Pvt. Ltd.  A/C Semi Sleeper (2+2)          19:30   
720  Indo Canadian Transport Pvt. Ltd.       A/C Sleeper (2+1)          22:00   
721  Indo Canadian Transport Pvt. Ltd.  A/C Semi Sleeper (2+2)          14:30   
722  Indo Canadian Transport Pvt. Ltd.  A/C Semi Sleeper (2+2)          06:00   

    duration reaching_time star_rating     price   seat_availability  \
0    06h 35m         13:15     4.0\n56   INR 845  38 Seats available   
1    07h 00m         17:15     4.0\n19   INR 845  33 Seats available   
2    07h 30m         22:30      2.0\n9   INR 845  37 Seats available   
3    07h 00m         23:10     4.2\n16   INR 845  35 Seats available   
4    08h 00m         01:35         4.1   INR 845  35 Seats available   
..       ...           ...         ...       ...                 ...   
718  11h 45m         23:45         4.4  INR 2500  51 Seats available   
719  11h 45m         07:15         4.4  INR 2500  51 Seats available   
720  11h 45m         09:45         4.4  INR 3000  42 Seats available   
721  11h 45m         02:15         4.4  INR 3300  51 Seats available   
722  11h 45m         17:45         4.4  INR 3300  50 Seats available   

                         route_name  \
0             Ludhiana to Delhi Bus   
1             Ludhiana to Delhi Bus   
2             Ludhiana to Delhi Bus   
3             Ludhiana to Delhi Bus   
4             Ludhiana to Delhi Bus   
..                              ...   
718  Delhi Airport to Jalandhar Bus   
719  Delhi Airport to Jalandhar Bus   
720  Delhi Airport to Jalandhar Bus   
721  Delhi Airport to Jalandhar Bus   
722  Delhi Airport to Jalandhar Bus   

                                            route_link  
0    https://www.redbus.in/bus-tickets/ludhiana-to-...  
1    https://www.redbus.in/bus-tickets/ludhiana-to-...  
2    https://www.redbus.in/bus-tickets/ludhiana-to-...  
3    https://www.redbus.in/bus-tickets/ludhiana-to-...  
4    https://www.redbus.in/bus-tickets/ludhiana-to-...  
..                                                 ...  
718  https://www.redbus.in/bus-tickets/delhi-airpor...  
719  https://www.redbus.in/bus-tickets/delhi-airpor...  
720  https://www.redbus.in/bus-tickets/delhi-airpor...  
721  https://www.redbus.in/bus-tickets/delhi-airpor...  
722  https://www.redbus.in/bus-tickets/delhi-airpor...  

[723 rows x 10 columns]

In [21]:
#change dataframe to csv

df_pepsu_details.to_csv('pepsu_buses.csv', index=False)

BSRTC Bus Details

In [7]:
#read csv file
df=pd.read_csv("bsrtc_routes.csv")
df

Route name  \
0                 Patna (Bihar) to Bettiah   
1               Gopalganj (Bihar) to Delhi   
2                Patna (Bihar) to Motihari   
3                        Delhi to Motihari   
4                 Bettiah to Patna (Bihar)   
5                        Motihari to Delhi   
6   Patna (Bihar) to Balmiki Nagar (bihar)   
7   Balmiki Nagar (bihar) to Patna (Bihar)   
8               Patna (Bihar) to Kathmandu   
9                 Patna (Bihar) to Katihar   
10                 Patna (Bihar) to Purnea   
11             Patna (Bihar) to Hazaribagh   
12                 Ranchi to Patna (Bihar)   
13             Hazaribagh to Patna (Bihar)   
14                 Patna (Bihar) to Raxaul   
15        Muzaffarpur (Bihar) to Kathmandu   
16                 Patna (Bihar) to Ranchi   
17           Muzaffarpur (Bihar) to Ranchi   
18              Kathmandu to Patna (Bihar)   
19           Ranchi to Muzaffarpur (Bihar)   
20                     Motihari to Lucknow   
21                     Lucknow to Motihari   
22                   Motihari to Kathmandu   
23                        Agra to Motihari   
24       Patna (Bihar) to Janakpur (Nepal)   
25       Muzaffarpur (Bihar) to Hazaribagh   
26                 Purnea to Patna (Bihar)   
27         Patna (Bihar) to Araria (Bihar)   
28              Darbhanga to Patna (Bihar)   
29                Patna (Bihar) to Saharsa   
30                        Motihari to Agra   
31            Hajipur (Bihar) to Kathmandu   
32                   Kathmandu to Motihari   
33             Patna (Bihar) to Forbesganj   
34               Ranchi to Hajipur (Bihar)   
35            Lucknow to Gopalganj (Bihar)   

                                           Route link  
0   https://www.redbus.in/bus-tickets/patna-to-bet...  
1   https://www.redbus.in/bus-tickets/gopalganj-to...  
2   https://www.redbus.in/bus-tickets/patna-to-mot...  
3   https://www.redbus.in/bus-tickets/delhi-to-mot...  
4   https://www.redbus.in/bus-tickets/bettiah-to-p...  
5   https://www.redbus.in/bus-tickets/motihari-to-...  
6   https://www.redbus.in/bus-tickets/patna-to-bal...  
7   https://www.redbus.in/bus-tickets/balmiki-naga...  
8   https://www.redbus.in/bus-tickets/patna-to-kat...  
9   https://www.redbus.in/bus-tickets/patna-to-kat...  
10  https://www.redbus.in/bus-tickets/patna-to-purnea  
11  https://www.redbus.in/bus-tickets/patna-to-haz...  
12  https://www.redbus.in/bus-tickets/ranchi-to-patna  
13  https://www.redbus.in/bus-tickets/hazaribagh-t...  
14  https://www.redbus.in/bus-tickets/patna-to-raxaul  
15  https://www.redbus.in/bus-tickets/muzaffarpur-...  
16  https://www.redbus.in/bus-tickets/patna-to-ranchi  
17  https://www.redbus.in/bus-tickets/muzaffarpur-...  
18  https://www.redbus.in/bus-tickets/kathmandu-to...  
19  https://www.redbus.in/bus-tickets/ranchi-to-mu...  
20  https://www.redbus.in/bus-tickets/motihari-to-...  
21  https://www.redbus.in/bus-tickets/lucknow-to-m...  
22  https://www.redbus.in/bus-tickets/motihari-to-...  
23  https://www.redbus.in/bus-tickets/agra-to-moti...  
24  https://www.redbus.in/bus-tickets/patna-to-jan...  
25  https://www.redbus.in/bus-tickets/muzaffarpur-...  
26  https://www.redbus.in/bus-tickets/purnea-to-patna  
27  https://www.redbus.in/bus-tickets/patna-to-araria  
28  https://www.redbus.in/bus-tickets/darbhanga-to...  
29  https://www.redbus.in/bus-tickets/patna-to-sah...  
30  https://www.redbus.in/bus-tickets/motihari-to-...  
31  https://www.redbus.in/bus-tickets/hajipur-to-k...  
32  https://www.redbus.in/bus-tickets/kathmandu-to...  
33  https://www.redbus.in/bus-tickets/patna-to-for...  
34  https://www.redbus.in/bus-tickets/ranchi-to-ha...  
35  https://www.redbus.in/bus-tickets/lucknow-to-g...

In [9]:
driver = webdriver.Chrome()

#Creating a list to store bus details

bus_details = []

#looping the each route links in the  dataframe :

for i in df["Route link"]:

    driver.get(i) #

    full_url = driver.current_url
    driver.get(full_url + f'&onward=14-Aug-2024')

    time.sleep(2)  # Let the page load
    driver.maximize_window()
    
    # To get route name and route links
    try:
        route_name = driver.find_element(By.CLASS_NAME, 'D136_h1').text
        route_link = driver.current_url
    except Exception as e:
        print(f"Error retrieving route name or link: {e}")
        continue
    
    # Initialize WebDriverWait
    wait = WebDriverWait(driver, 20)  # Increased timeout

    # Wait for buttons to be visible and click them
    try:
        govt_buttons = wait.until(EC.visibility_of_all_elements_located((By.XPATH, './/div[@class="button"]')))
        for govt_button in govt_buttons[::-1]:
                driver.execute_script("window.scrollTo(0, 330);")
                govt_button.click()
                time.sleep(2)
                
    except Exception as e:
        print(f"Error waiting for buttons: {e}")
        continue

    # Scroll down to load more buses
    scroll_to_load(driver, 10)

    # Wait until all  bus items  present
    try:
        wait.until(EC.presence_of_all_elements_located((By.CLASS_NAME, 'bus-item')))
        containers = driver.find_elements(By.CLASS_NAME, 'bus-item')
        for container in containers:
            try:
                bus_names = container.find_element(By.XPATH, './/div[@class="travels lh-24 f-bold d-color"]').text
                bus_type = container.find_element(By.XPATH, './/div[@class="bus-type f-12 m-top-16 l-color evBus"]').text
                departure_time = container.find_element(By.XPATH, './/div[@class="dp-time f-19 d-color f-bold"]').text
                duration = container.find_element(By.XPATH, './/div[@class="dur l-color lh-24"]').text
                reaching_time = container.find_element(By.XPATH, './/div[@class="bp-time f-19 d-color disp-Inline"]').text
                star_rating = container.find_element(By.XPATH,".//div[@class='column-six p-right-10 w-10 fl']").text
                price = container.find_element(By.XPATH, './/div[@class="fare d-block"]').text
                seat_availability = container.find_element(By.XPATH, './/div[contains(@class,"seat-left")]').text

                 
                bus_details.append({
                    "bus_name": bus_names,
                    "bus_type": bus_type,
                    "departure_time": departure_time,
                    "duration": duration,
                    "reaching_time": reaching_time,
                    "star_rating": star_rating,
                    "price": price,
                    "seat_availability": seat_availability,
                    "route_name": route_name,
                    "route_link": route_link
                })
            except Exception as e:
                print(f"Error extracting details: {e}")
    except Exception as e:
        print(f"Error waiting for bus items: {e}")

    

# Print the collected bus details
print(bus_details)



Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waiting for buttons: Message: 

Error waitin

In [10]:
# Converting into DATAFRAME 

df_bsrtc_details=pd.DataFrame(bus_details)
df_bsrtc_details

bus_name  \
0    Bihar state road transport corporation (BSRTC)...   
1    Bihar state road transport corporation (BSRTC)...   
2                         Jai Mata Di Tour and Travels   
3                                        V.I.P Travels   
4                                  Jai Hanuman Travels   
..                                                 ...   
97   Bihar state road transport corporation (BSRTC)...   
98                                      Panwar Travels   
99                     Baba Khatushyam Travels Pvt Ltd   
100                             Travel Point World LLP   
101                    Shree Balajee Travels And Cargo   

                       bus_type departure_time duration reaching_time  \
0           Non AC Seater (2+2)          06:00  05h 00m         11:00   
1               AC Seater (2+2)          06:30  06h 05m         12:35   
2    A/C Seater / Sleeper (2+2)          20:28  05h 32m         02:00   
3    A/C Seater / Sleeper (2+2)          21:40  06h 00m         03:40   
4    A/C Seater / Sleeper (2+2)          22:20  06h 40m         05:00   
..                          ...            ...      ...           ...   
97          Volvo AC Seater 2+2          17:20  14h 40m         08:00   
98            A/C Sleeper (2+1)          15:40  14h 35m         06:15   
99   A/C Seater / Sleeper (3+1)          17:35  13h 55m         07:30   
100  A/C Seater / Sleeper (2+2)          18:20  12h 30m         06:50   
101  A/C Seater / Sleeper (2+1)          15:00  15h 43m         06:43   

    star_rating     price   seat_availability            route_name  \
0      3.8\n121   INR 285  25 Seats available  Patna to Bettiah Bus   
1      3.4\n161   INR 331   5 Seats available  Patna to Bettiah Bus   
2        3.4\n5       450   6 Seats available  Patna to Bettiah Bus   
3           3.0   INR 350  61 Seats available  Patna to Bettiah Bus   
4       3.7\n37   INR 550  54 Seats available  Patna to Bettiah Bus   
..          ...       ...                 ...                   ...   
97       2.3\n7  INR 1300  44 Seats available  Motihari to Agra Bus   
98          2.8  INR 2500  26 Seats available  Motihari to Agra Bus   
99          1.7  INR 1199  57 Seats available  Motihari to Agra Bus   
100         1.5      1899  38 Seats available  Motihari to Agra Bus   
101         1.2  INR 1799  47 Seats available  Motihari to Agra Bus   

                                            route_link  
0    https://www.redbus.in/bus-tickets/patna-to-bet...  
1    https://www.redbus.in/bus-tickets/patna-to-bet...  
2    https://www.redbus.in/bus-tickets/patna-to-bet...  
3    https://www.redbus.in/bus-tickets/patna-to-bet...  
4    https://www.redbus.in/bus-tickets/patna-to-bet...  
..                                                 ...  
97   https://www.redbus.in/bus-tickets/motihari-to-...  
98   https://www.redbus.in/bus-tickets/motihari-to-...  
99   https://www.redbus.in/bus-tickets/motihari-to-...  
100  https://www.redbus.in/bus-tickets/motihari-to-...  
101  https://www.redbus.in/bus-tickets/motihari-to-...  

[102 rows x 10 columns]

In [11]:
#change dataframe to csv

df_bsrtc_details.to_csv('bsrtc_buses.csv', index=False)